# 프로젝트 - 로컬팜 서비스 현황 분석



---



# 분석을 위한 기본 설정

## 기본 라이브러리 설정

In [ ]:
!pip install pandas folium

In [ ]:
import pandas as pd 
import numpy as np
import folium

## Google Drive 마운트

In [ ]:
# from google.colab import drive
# drive.mount('/content/drive')

## BigQuery 연동을 위한 기본 설정

In [ ]:
from google.colab import auth
from google.cloud import bigquery
from google.colab import data_table

project = 'crypto-song-379002' # Project ID inserted based on the query results selected to explore
location = 'US' # Location inserted based on the query results selected to explore
client = bigquery.Client(project=project, location=location)
data_table.enable_dataframe_formatter()
auth.authenticate_user()



---



# 로컬팜의 현재 상황 및 주요 이슈 

> **분석 진행에 앞서 수강생 분들께 전달되는 가상의 업체 상황**
- 21년 7월 목동의 유승상가에 픽업존 운영을 시작으로 현재는 총 8개의 매장을 운영중
- 22년 11월 서울지역 과일전문 다판다마켓을 인수(10월 말 부터 시범판매 시작, 11월 둘째주에 매장 오픈) 
- 물품을 소싱하는 판매자는 최초 (김지은-4f1d3d66, 양민석-34e92532, 손미경-afe78ffc) 3명으로 시작하였으나, 다판다마켓 인수와 함께 10월 부터 (김정식-2cca8b6e)님 합류.
- 현재 내부 인력의 대부분은 상품 소싱 및 배송에 투입되어, 사용자 특징이나 앱 서비스 개선점 등에 대해서는 정확히 파악하지 못하고 있음.
- 최근에는 매출을 올리기 위해 매장을 늘리는게 좋을지, 기존 매장관리에 주력하는게 좋을지 고민하고 있으나 뚜렷한 답을 찾지 못한 상황.



---



# **[결론 및 제언]**

**1. 사용자 유입 현황**
  - 다판다마켓 기존 유저들의 대량유입으로 11월 MAU는 역대 최고 수준인 6,352명 달성했으나 (전월比 55% 상승)
  - 다판다마켓 인수 이전 8월부터 10월까지는 MAU가 지속 하락세에 있었으며 
  - 신규 유저 또한 모객 시점이 22년 하반기로 갈수록 M+1 재접속률이 떨어지는 추세

**2. 잔존율 현황**
  - 11월 2주차에 다판다마켓 유저들이 대거 유입되면서 신규 유저의 11월 일평균 D+1 잔존율이 일시적으로 상승했으며 (전월比 40.8%p 상승한 69.4%)
  - 11월 재방문 유저의 일평균 D+1 잔존율 또한 전월比 3.8%p 상승한 64.5% 달성

**3. 매출 현황**
  - 다판다마켓 인수의 영향으로 11월 매출 1.4억원 달성 (전월比 160% 상승) 
  - 신규상품 공급에 따라 기존 로컬팜 매장의 11월 매출이 전월比 24 ~ 52% 상승했으며
  - 신규상품을 통해 발생한 매출 중 50% 이상이 기존 유저들로 부터 발생

**4. 구매형태**
  - 과반 이상의 결제유저가 한달에 4만원 이하 또는 2회 이하로 상품을 구매하고 있으며
  - 메이비카페점의 제외한 나머지 매장의 경우, 결제 유저의 90% 이상이 거주지와 매장간의 거리가 1km 이내로 측정됨 

**5. 제언**
  - **다판다마켓 인수 및 신규 상품 공급의 영향으로 11월 MAU와 매출이 대폭 상승하였으나, 오프라인 매장 특성상 신규상품의 지속적인 공급 없이는 추가적인 매출 상승이 어려울 것으로 예상됨**
  - **지속적인 신규 상품 공급을 위해서는 아래의 두 가지 문제 해결이 선행되어야 할 것으로 판단됨**
    - 픽업 매장으로의 물류 배송/분배 최적화 - 기존 판매자들이 비효율적인 배송망으로 인해 신규 상품 소싱에 사용할 리소스 부족
    - 플랫폼 사용자(판매자) 확대 - 내부 셀러들로만 신규 상품을 지속적으로 공급하는데 한계가 있음

---

# **[ 오프라인 매장 현황 ]**

## < 매장 정보 >

In [ ]:
#@title Make DataFrame

## << shopsInfosDf: 매장 정보 테이블 생성 >>
query_job = client.query("""
    with shopinfos as (
      select a.pickup_shop_name, b.order_year_month
           , sum(b.payment_amount) as sales
      from (
        -- 매장 정보 테이블
        select pickup_shop_name
        from `crypto-song-379002.localparm_dw.pickup_shop`
      ) as a
      inner join (
        -- 매장별 결제 테이블
        select order_date, order_year_month
             , payment_amount, pickup_shop_name
        from `crypto-song-379002.my_temp.orders`
        where payment_status= 'completed' -- 결제 완료건만 집계
      ) as b
      on a.pickup_shop_name = b.pickup_shop_name
      group by a.pickup_shop_name, order_year_month
    )

    select pickup_shop_name, order_year_month, sales
    from(
      select pickup_shop_name, order_year_month, sales
      from shopinfos 

      union all

      select '픽업존(통합)' as pickup_shop_name, order_year_month, sum(sales) as sales
      from shopinfos
      group by order_year_month
    ) as a
    order by case when pickup_shop_name = '픽업존(통합)' then 0
                  when pickup_shop_name = '픽업존(유승상가)' then 1
                  when pickup_shop_name = '픽업존(메이비카페)' then 2 
                  when pickup_shop_name = '픽업존(서울드림신용협동조합)' then 3 
                  when pickup_shop_name = '픽업존(GS25 목동3동점)' then 4 
                  when pickup_shop_name = '픽업존(참맛부대찌개아구찜)' then 5 
                  when pickup_shop_name = '픽업존(GS영등포당산점)' then 6 
                  when pickup_shop_name = '픽업존(다이소 난곡사거리점)' then 7 
                  when pickup_shop_name = '픽업존(더현대서울)' then 8 
              end
            , order_year_month

""")

shopsInfosDf = query_job.to_dataframe()


##------------------------------------------------------------------------------------------------------------------------------------------------------------------------##

## << shopsInfosDf: 매장 정보 테이블 생성 >>

query_job = client.query("""
    with shopinfos as (
      select case when a.pickup_shop_name is null then '픽업존(통합)' else a.pickup_shop_name end as pickup_shop_name
           , case when a.pickup_shop_name is not null then a.region_1depth_name else '서울' end as region_1depth_name  
           , case when a.pickup_shop_name is not null then a.region_2depth_name else '-' end as region_2depth_name  
           , case when a.pickup_shop_name is not null then a.region_3depth_name else '-' end as region_3depth_name  
           , case when a.pickup_shop_name is null or a.pickup_shop_name = '픽업존(유승상가)' then '2021-07-22' 
                  else min(order_date) 
             end as shop_open_date -- (사업 담당자에게 확인한 정보를 기준으로) 최초 오픈일 수정
      from (
        -- 매장 정보 테이블
        select pickup_shop_name
             , region_1depth_name, region_2depth_name, region_3depth_name
        from `crypto-song-379002.localparm_dw.pickup_shop`
      ) as a
      inner join (
        -- 매장별 결제 테이블
        select order_date, order_year_month
             , payment_amount, pickup_shop_name
        from `crypto-song-379002.my_temp.orders`
        where payment_status= 'completed' -- 결제 완료건만 집계
      ) as b
      on a.pickup_shop_name = b.pickup_shop_name
      group by rollup(a.pickup_shop_name, a.region_1depth_name, a.region_2depth_name, a.region_3depth_name)
    )

    select * 
    from shopinfos
    where region_3depth_name is not null
    order by case when pickup_shop_name = '픽업존(통합)' then 0
             when pickup_shop_name = '픽업존(유승상가)' then 1
             when pickup_shop_name = '픽업존(메이비카페)' then 2 
             when pickup_shop_name = '픽업존(서울드림신용협동조합)' then 3 
             when pickup_shop_name = '픽업존(GS25 목동3동점)' then 4 
             when pickup_shop_name = '픽업존(참맛부대찌개아구찜)' then 5 
             when pickup_shop_name = '픽업존(GS영등포당산점)' then 6 
             when pickup_shop_name = '픽업존(다이소 난곡사거리점)' then 7 
             when pickup_shop_name = '픽업존(더현대서울)' then 8 
          end
""")
shopsRegionInfosDf = query_job.to_dataframe()

In [ ]:
#@title Visualization

import plotly.graph_objects as go
import plotly.figure_factory as ff

## 참고 예제코드 : https://plotly.com/python/figure-factory-subplots/ 😉
## figure_factory package: https://plotly.com/python-api-reference/generated/plotly.figure_factory.html

## step.1 - 오프라인 매장 정보 테이블 생성
fig = ff.create_table(shopsRegionInfosDf.rename(columns={'pickup_shop_name':'매장',
                                                         'region_1depth_name': '지역1',
                                                         'region_2depth_name': '지역2',
                                                         'region_3depth_name': '지역3',
                                                         'shop_open_date': '오픈일',
                                                         }))
for i in range(len(fig.layout.annotations)): # 생성된 테이블을 순차적으로 돌면서 폰트 사이즈를 10으로 설정
  fig.layout.annotations[i].font.size = 10


## step.2 - 오프라인 매장 월별 매출 추이 도식
trace1 = go.Scatter(x=shopsInfosDf[shopsInfosDf['pickup_shop_name'] == "픽업존(통합)"]["order_year_month"], 
                    y=shopsInfosDf[shopsInfosDf['pickup_shop_name'] == "픽업존(통합)"]["sales"],
                    name='픽업존(통합)',
                    line=dict(width=4, dash='dot'), # e.g., dash = 'dot', dash = 'dash'
                    xaxis='x2', yaxis='y2')

trace2 = go.Scatter(x=shopsInfosDf[shopsInfosDf['pickup_shop_name'] == "픽업존(유승상가)"]["order_year_month"], 
                    y=shopsInfosDf[shopsInfosDf['pickup_shop_name'] == "픽업존(유승상가)"]["sales"],
                    name='픽업존(유승상가)',
                    xaxis='x2', yaxis='y2')

trace3 = go.Scatter(x=shopsInfosDf[shopsInfosDf['pickup_shop_name'] == "픽업존(메이비카페)"]["order_year_month"], 
                    y=shopsInfosDf[shopsInfosDf['pickup_shop_name'] == "픽업존(메이비카페)"]["sales"],
                    name='픽업존(메이비카페)',
                    xaxis='x2', yaxis='y2')

trace4 = go.Scatter(x=shopsInfosDf[shopsInfosDf['pickup_shop_name'] == "픽업존(서울드림신용협동조합)"]["order_year_month"], 
                    y=shopsInfosDf[shopsInfosDf['pickup_shop_name'] == "픽업존(서울드림신용협동조합)"]["sales"],
                    name='픽업존(서울드림신용협동조합)',
                    xaxis='x2', yaxis='y2')

trace5 = go.Scatter(x=shopsInfosDf[shopsInfosDf['pickup_shop_name'] == "픽업존(GS25 목동3동점)"]["order_year_month"], 
                    y=shopsInfosDf[shopsInfosDf['pickup_shop_name'] == "픽업존(GS25 목동3동점)"]["sales"],
                    name='픽업존(GS25 목동3동점)',
                    xaxis='x2', yaxis='y2')

trace6 = go.Scatter(x=shopsInfosDf[shopsInfosDf['pickup_shop_name'] == "픽업존(참맛부대찌개아구찜)"]["order_year_month"], 
                    y=shopsInfosDf[shopsInfosDf['pickup_shop_name'] == "픽업존(참맛부대찌개아구찜)"]["sales"],
                    name='픽업존(참맛부대찌개아구찜)',
                    xaxis='x2', yaxis='y2')

trace7 = go.Scatter(x=shopsInfosDf[shopsInfosDf['pickup_shop_name'] == "픽업존(GS영등포당산점)"]["order_year_month"], 
                    y=shopsInfosDf[shopsInfosDf['pickup_shop_name'] == "픽업존(GS영등포당산점)"]["sales"],
                    name='픽업존(GS영등포당산점)',
                    xaxis='x2', yaxis='y2')

trace8 = go.Scatter(x=shopsInfosDf[shopsInfosDf['pickup_shop_name'] == "픽업존(다이소 난곡사거리점)"]["order_year_month"], 
                    y=shopsInfosDf[shopsInfosDf['pickup_shop_name'] == "픽업존(다이소 난곡사거리점)"]["sales"],
                    name='픽업존(다이소 난곡사거리점)',
                    xaxis='x2', yaxis='y2')

trace9 = go.Scatter(x=shopsInfosDf[shopsInfosDf['pickup_shop_name'] == "픽업존(더현대서울)"]["order_year_month"], 
                    y=shopsInfosDf[shopsInfosDf['pickup_shop_name'] == "픽업존(더현대서울)"]["sales"],
                    name='픽업존(더현대서울)',
                    xaxis='x2', yaxis='y2')

fig.add_traces([trace1, trace2, trace3, trace4, trace5, trace6, trace7, trace8, trace9])


## step.3 - 그래프 레이아웃 수정

# initialize xaxis2 and yaxis2
fig['layout']['xaxis2'] = {}
fig['layout']['yaxis2'] = {}

# Edit layout for subplots
fig.layout.xaxis.update({'domain': [0, 0.5]})
fig.layout.xaxis2.update({'domain': [0.6, 1.]})

# The graph's yaxis MUST BE anchored to the graph's xaxis
fig.layout.yaxis2.update({'anchor': 'x2'})
fig.layout.yaxis2.update({'title': 'SALES(원)'})

# Update the margins to add a title and see graph x-labels.
fig.layout.margin.update({'t':50, 'b':50})
# fig.layout.update({'title': '로컬팜 오프라인매장 위치'})


## Step.4 - 그래프 마우스 오버시 hovermode x축으로 설정
fig.update_layout(hovermode="x")

## Step.5 - fig의 layout 설정 변경
fig.update_layout(
    {
        "title": {
            "text": "<b>< 오프라인 매장 정보 및 월매출 추이 ><b>",
            "x": 0.5,
            "y": 0.98,
            "font": {
                "size": 15
            }
        },
        "xaxis2": {
            "tick0": "2022-05",
            "dtick": 'M1',
            "tickformat": "%Y-%m"
        },
        "height": 500,
    },
)

## step.6 - 오프라인 매장 월별 매출 추이 도식
fig.show()

> **Note**

- 11월에 오픈한 (GS영등포당산점, 다이소 난곡사거리점)은 기존 다판다마켓의 판매지역이며, (더현대서울) 지점은 서울시 창업지원을 받아 입점 

> **Comment**

- 전체 매장의 11월 매출은 전월比 160% 상승
- 유승상가 지점의 경우 5월 이후 지속적인 매출 하락세였으나 11월에 전월比 매출 78% 상승
- 6월에 신규 오픈한 4개 지점 또한 8월 이후 매출 하락세에 들어갔으나 11월에 전월比 매출 (23% ~ 136%) 상승
- 11월에 신규 입점한 2개(GS영등포당산점, 다이소 난곡사거리점) 지점의 경우 11월 전체 매출의 약 30% 차지

## < 오프라인 매장 및 결제유저 분포 >

In [ ]:
#@title Make DataFrame-1

## << 11월 데이터 기준 - 매장별 결제 유저별 거주지 및 11월 누적 결제액  >>
query_job = client.query("""
    select a.user_id, b.x, b.y, a.pickup_shop_name, sum(payment_amount) as payment_amount
    from (
      -- 11월 결제 데이터
      select *
      from `crypto-song-379002.my_temp.orders`
      where order_year_month = '2022-11'
        and payment_status = 'completed'
    ) as a
    inner join (
      -- 사용자 가입 정보(거주지)
      select *
      from `crypto-song-379002.my_temp.my_infos`
    ) as b
    on a.user_id = b.user_id
    group by a.user_id, b.x, b.y, a.pickup_shop_name
""")
novPickupUniquePu = query_job.to_dataframe()


## << 오프라인 매장 위치 >>
storesRegionDf = pd.DataFrame({
    'pickup_shop_name':['픽업존(메이비카페)', '픽업존(다이소 난곡사거리점)', '픽업존(서울드림신용협동조합)', '픽업존(참맛부대찌개아구찜)', '픽업존(GS영등포당산점)', '픽업존(유승상가)', '픽업존(GS25 목동3동점)', '픽업존(더현대서울)'],
    'region_1depth_name':['서울', '서울', '서울', '서울', '서울', '서울', '서울', '서울'],
    'region_2depth_name':['구로구', '관악구', '구로구', '영등포구', '영등포구', '양천구', '양천구', '영등포구'],
    'region_3depth_name':['구로동', '신림동', '신도림동', '문래동3가', '당산동5가', '목동', '목동', '여의도동'],
    'h_code':[1153054000, 1162076500, 1153051000, 1156060500, 1156056000, 1147055000, 1147053000, 1156054000],
    'x':[37.4849288, 37.48145951, 37.5095675, 37.51627575, 37.53237867, 37.5398954, 37.54638929, 37.52519132],
    'y':[126.9002594, 126.9142068, 126.8820361, 126.8973904, 126.8968009, 126.881942, 126.8644345, 126.9291128],
    
})

In [ ]:
#@title Make DataFrame-2

## << novShopAndPuRegion: 11월 매출 기준 매장별 구매자 거주지역별 매출 >>
query_job = client.query("""

-- 지역별 구매유저 결제정보
with pu_region as (
  select a.user_id, a.order_year_month, a.order_date, a.payment_amount, a.pickup_shop_name, concat(b.region_2depth_name, '_', b.region_3depth_name) as region
  from `my_temp.orders` as a
  left join `my_temp.my_infos` as b
  on a.user_id = b.user_id
)

-- 11월 매장별, 지역별, 월별 누적 매출
select order_year_month, pickup_shop_name, region
     , sum(payment_amount) as sales
     , round(sum(payment_amount)/sum(sum(payment_amount)) over(partition by pickup_shop_name), 3) as ratio_of_sales
from pu_region
group by order_year_month, pickup_shop_name, region
having order_year_month = '2022-11'
order by case when pickup_shop_name = '픽업존(유승상가)' then 1
              when pickup_shop_name = '픽업존(메이비카페)' then 2 
              when pickup_shop_name = '픽업존(서울드림신용협동조합)' then 3 
              when pickup_shop_name = '픽업존(GS25 목동3동점)' then 4 
              when pickup_shop_name = '픽업존(참맛부대찌개아구찜)' then 5 
              when pickup_shop_name = '픽업존(GS영등포당산점)' then 6 
              when pickup_shop_name = '픽업존(다이소 난곡사거리점)' then 7 
              when pickup_shop_name = '픽업존(더현대서울)' then 8 
          end
       , ratio_of_sales desc

""")

novShopAndPuRegion = query_job.to_dataframe()

In [ ]:
#@title Visualization-1

## Folium Document > https://python-visualization.github.io/folium/  <- Quick Start 부분을 참고해 주세요 😉 
from folium.plugins import MarkerCluster 

## << 핀 포인트 - 초기 지도 위치 설정 >>
latitude = 37.5161 # 위도
longitude = 126.8967 # 경도

f = folium.Figure(height=750) ##  Colab 코드셀 & folium map - Height 동시 조절
m = folium.Map(
    location=[latitude, longitude],
    zoom_start=13,
).add_to(f)

mrkerCluster = MarkerCluster().add_to(m)  

## << 매장 위치 표시 >>
for lat, long, name in zip(storesRegionDf['x'], storesRegionDf['y'], storesRegionDf['pickup_shop_name']):
    folium.Marker(location = [lat, long], popup=name, icon=folium.Icon(color='red', icon='star')).add_to(m)

## << 구매 유저 위치 표시 >>
for lat, long in zip(novPickupUniquePu['x'], 
                     novPickupUniquePu['y']):
    folium.Marker([lat, long], icon = folium.Icon(color="blue")).add_to(mrkerCluster)
    
m

In [ ]:
#@title Visualization-2

## << 지역별 MAU - Bar Chart >>

import plotly.express as px

## Step.1 - fig에 px.bar() 그래프 담기
fig = px.bar(novShopAndPuRegion, 
              x="pickup_shop_name", 
              y="ratio_of_sales", 
              color= "region",
              color_discrete_sequence=px.colors.qualitative.Dark24, # https://plotly.com/python/discrete-color/#color-sequences-in-plotly-express
              text="ratio_of_sales",
             )


# ## Step.2 - text 표현 형식과, 출력 위치를 조정 / 호버 텍스트 포멧 조정
fig.update_traces(texttemplate='%{text:.1%}', textposition='inside') 
fig.update_traces(hovertemplate = "매출비중: %{text:.1%}" )


# ## Step.3 - fig의 layout 설정 변경
fig.update_layout(
    {
        "title": {
            "text": "<b>< 11월 - 매장별 결제유저 거주지역별 매출 비중 ><b>",
            "x": 0.5,
            "y": 0.95,
            "font": {
                "size": 13
            }
        },
        "xaxis": { "title": "", },
        "yaxis": { "title": "매출비중(%)", "tickformat": '.0%' }, 
        "legend_title_text": "거주지역",
        "legend": { "traceorder": "normal"},
        "template":'plotly_white',
        "height": 280,
    }
)

## Step.4 - 그래프 마우스 오버시 hovermode x축으로 설정
fig.update_layout(hovermode="x")


## Step.5 - 그래프 출력
fig.show()

> **Comment**

- 유사한 입지 임에도 매장별로 매출 규모나 사용자 거주지역 분포에 차이가 나는 것으로 보아 매장별 구매형태(거리/누적구매액/누적구매횟수/선호상품) 비교 분석을 통해 차별화된 판매전략 수립 필요

# **[ 사용자 유입 현황 분석 ]**

## < 요약 ✨ >


> **다판다마켓 인수 및 신규매장 오픈 효과**
  - 11월 MAU는 역대 최고 수준인 6,352명 달성 (전월比 55% 증가)
  - 기존 사용자 거주지역 중 8개 지역은 10월比 11월 MAU가 30%이상 증가했으며, 각 지역별 증가분의 평균 82%는 신규유입을 통해 발생 
    - 8개 지역 - 대림2동, 당산동5가, 당상동4가, 신림동, 조원동, 구로2동, 독산3동, 양평동3가

> **기존 유저들의 이탈 속도 증가**
  - 22년 가입 유저군의 경우 사용자의 신규 유입보다 이탈 속도가 빨라 8월 ~ 10월 동안 MAU 하락세에 있었으며
  - 특히 유저들의 모객 시점이 22년 하반기로 갈수록 이탈속도가 빨라지고 있음
  - 이러한 이탈 가속 현상은 다수의 지역에서 공통적으로 발생하고 있으므로 추후 별도의 이탈 원인 분석 필요


## < MAU, NRU >

In [ ]:
#@title Make DataFrame ⛳️

## << mauDf: 월간 활성 유저수 >>
query_job = client.query("""
    select login_year_month
         , count(distinct user_id) as login_user_cnt
    from `crypto-song-379002.my_temp.daily_login_users`
    group by login_year_month
    order by login_year_month    
""")
mauDf = query_job.to_dataframe()

## << monthlyNruDf: 월간 가입 유저수 >>
query_job = client.query("""
    select create_year_month, count(distinct user_id) as user_cnt
    from `crypto-song-379002.my_temp.my_infos`
    group by create_year_month
    order by create_year_month
""")
monthlyNruDf = query_job.to_dataframe()

In [ ]:
#@title Visualization ⛳️
import plotly.graph_objects as go

## Step.1 - 강조하고 싶은 부분만 crimson 색으로 표시
#  색상 참고: https://www.devkuma.com/docs/html/html-%EC%83%89-color/
colors = ['lightgray',] * len(mauDf)
colors[len(mauDf) - 1] = 'crimson'

## Step.2 - fig안에 go.Bar(), go.Scatter() 그래프 담기
fig = go.Figure()
fig.add_trace(
    go.Bar(    
        x=mauDf['login_year_month'], 
        y=mauDf['login_user_cnt'],
        name='MAU(월간 활성 유저수)',
        text=mauDf['login_user_cnt'], 
        textposition='auto', 
        texttemplate='%{text:,}명',
        marker_color=colors # MAU 11월 색 강조
    )
)

fig.add_trace(
    go.Scatter(
        x=monthlyNruDf[monthlyNruDf['create_year_month'] >= '2022-01']['create_year_month'],
        y=monthlyNruDf[monthlyNruDf['create_year_month'] >= '2022-01']['user_cnt'],
        name='NRU(신규 유저수)', 
        mode='lines+markers+text', 
        text=monthlyNruDf[monthlyNruDf['create_year_month'] >= '2022-01']['user_cnt'],  
        textposition='top center',
        texttemplate='%{text:,}명',
    )
)

## Step.2 - fig의 layout 설정 변경
fig.update_layout(
    {
        "title": {
            "text": "<b>< 월간 MAU, NRU ><b>",
            "x": 0.5,
            "y": 0.9,
            "font": {
                "size": 13
            }
        },
        "yaxis": {
            "title": "MAU, NRU(명)", "tickformat": ','
        },
        "xaxis": {
            "tick0": "2022-01",
            "dtick": 'M1',
            "tickformat": "%Y-%m"
        },
        "template":'plotly_white',
        "legend": {'orientation': 'h', 'x': 0, 'y': 1.2}
    },
)

## [참고] fig의 layout 속성중 일부를, 개별적으로 설정해 주는 방법도 있습니다. 
#  ㄴ dict()함수는 https://wikidocs.net/16 참고!
# fig.update_layout(legend = dict(orientation = "h",
#                                 x=0,
#                                 y=1.2,
# ))
#

## Step.3 - fig의 y축을 기준으로, 직사각형 영역 표시 또는 텍스트를 남깁니다.
fig.add_vrect(x0="2021-12-15", 
              x1="2022-04-15",
              annotation_text="* 활성 유저수 지표는 22년 5월부터 확인 가능", 
              annotation_position="top left",
              fillcolor="black", opacity=0.1, line_width=0)

fig.add_vrect(x0="2022-07-18", 
              x1="2022-10-15",
              annotation_text="* MAU 점진적 하락 구간", 
              annotation_position="top left",
              fillcolor="hotpink", opacity=0.1, line_width=0)


## Step.4 - 그래프 출력 
fig.show(renderer='colab')

> **Comment**

- 7월 이후 MAU 볼륨이 점진적 하락 추세에 들어섰으나 11월 다판다마켓 인수 이후 6,352명 달성 (전월比 55% 증가) 
- 11월 NRU는 2,907명으로 전월比 258%(2,096명) 증가

## < 지역별 MAU, NRU >

In [ ]:
#@title Make DataFrame-1 ⛳️

## << mauByRegionDf: 월간 지역별 활성 유저수 >>
query_job = client.query("""
  
  -- 일간 접속유저 테이블(+ 거주지역) 
  with active_user as (
    select a.login_date, a.login_year_month, a.user_id, b.region_1depth_name, b.region_2depth_name, region_3depth_name
    from `crypto-song-379002.my_temp.daily_login_users` as a
    inner join `crypto-song-379002.my_temp.my_infos` as b
    on a.user_id = b.user_id
  ),

  -- 지역별 월간 접속유저 
  montly_active_user as (
     select region, login_year_month, user_cnt
         , lag(user_cnt, 1) over(partition by region order by login_year_month) as bef_1m_user_cnt
         , rank() over(partition by region order by login_year_month) as rank_asc -- 지역별 최초 접속 시점을 가려내기 위함
     from (
          -- 지역(region)별, 월별 MAU 집계
          select concat(region_2depth_name, '_', region_3depth_name) as region
               , login_year_month
               , count(distinct user_id) as user_cnt
          from active_user
          group by region, login_year_month
     ) as a
     order by region, login_year_month
  )

  select region, login_year_month
       , rank_asc
       , user_cnt
       , bef_1m_user_cnt
       , (user_cnt - bef_1m_user_cnt)/bef_1m_user_cnt as rate_of_change
       -- 각 지역별 11월 AU의 전월대비 증감률을 계산하고, 이를 통해 유저 그룹을 나눈다.
       , last_value((user_cnt - bef_1m_user_cnt)/bef_1m_user_cnt) over(partition by region order by login_year_month rows between unbounded preceding and unbounded following) as nov_rate_of_change
       , case when rank_asc = 1 and login_year_month = '2022-11' then 'new'
              when last_value((user_cnt - bef_1m_user_cnt)/bef_1m_user_cnt) over(partition by region order by login_year_month rows between unbounded preceding and unbounded following) < 0 then 'decrease'
              when last_value((user_cnt - bef_1m_user_cnt)/bef_1m_user_cnt) over(partition by region order by login_year_month rows between unbounded preceding and unbounded following) between 0 and 0.1 then 'increase_0_10'
              when last_value((user_cnt - bef_1m_user_cnt)/bef_1m_user_cnt) over(partition by region order by login_year_month rows between unbounded preceding and unbounded following) <= 0.2 then 'increase_10_20'
              when last_value((user_cnt - bef_1m_user_cnt)/bef_1m_user_cnt) over(partition by region order by login_year_month rows between unbounded preceding and unbounded following) <= 0.3 then 'increase_20_30'
              else 'increase_30_more'
         end as user_group
  from montly_active_user
  order by region, login_year_month
""")
mauByRegionDf = query_job.to_dataframe()

In [ ]:
#@title Visualization-1 ⛳️

## << 지역별 MAU - Bar Chart >>

import plotly.express as px

## Step.1 - fig에 px.bar() 그래프 담기
fig = px.bar(mauByRegionDf.rename(columns = {"user_cnt":"MAU"}), 
              x="login_year_month", 
              y="MAU", 
              color="region", 
              text="MAU",
              hover_data = {"login_year_month":False,} # 마우스 오버시 노출하고 싶지 않은 데이터 제외 처리
             )

## Step.2 - text 표현 형식과, 출력 위치를 조정 / 호버 텍스트 포멧 조정
fig.update_traces(texttemplate='%{text:,}명', textposition='inside') 

## Step.3 - fig의 layout 설정 변경
fig.update_layout(
    {
        "title": {
            "text": "<b>< 월간 지역별 MAU ><b>",
            "x": 0.5,
            "y": 0.95,
            "font": {
                "size": 13
            }
        },
        "yaxis": { "title": "MAU", "tickformat": ','  }, 
        "xaxis": {
            "title": "",
            "tick0": "2022-05",
            "dtick": 'M1',
            "tickformat": "%Y-%m"
        },
        "legend_title_text": "거주지역",
        "template":'plotly_white',
    }
)

## Step.4 - fig의 y축을 기준으로, 직사각형 영역 표시 또는 텍스트를 남깁니다.
fig.add_vrect(x0="2022-10-15", 
              x1="2022-11-17",
              annotation_text="* 11월 신규매장 오픈 이후, 기존 지역의 AU 볼륨 전월比 상승 (문래동3가 제외)", 
              annotation_position="top right",
              fillcolor="skyblue", opacity=0.25, line_width=0)

## Step.4 - 그래프 마우스 오버시 hovermode x축으로 설정
fig.update_layout(hovermode="x")

## Step.5 - 그래프 출력
fig.show()

> **Comment**

- 11월 신규 매장(GS영등포당산점, 다이소 난곡사거리점, 더현대서울)	오픈에 따라 여의도동, 양평동4가 지역주민이 신규로 유입되었으며
- 10월 기준 AU 볼륨이 500명 이하였던 지역들 위주로 11월 AU 30% 이상 증가 추세   

In [ ]:
#@title Make DataFrame-2 ⛳️

## << monthlyNruByRegionDf: 월간 지역별 가입 유저수 >>
query_job = client.query("""

  -- 신규 가입 유저 정보 테이블(+ region 컬럼 추가)
  with registere_user as (
    select user_id, create_date, create_year_month
         , region_1depth_name, region_2depth_name, region_3depth_name
         , concat(region_2depth_name, '_', region_3depth_name) as region
    from `crypto-song-379002.my_temp.my_infos`
  ),

  -- 지역(region)별, 월별 가입 유저수 테이블
  montly_registere_user as (
     select region, create_year_month, user_cnt
         , lag(user_cnt, 1) over(partition by region order by create_year_month) as bef_1m_user_cnt
         , rank() over(partition by region order by create_year_month) as rank_asc -- 지역별 최초 가입 시점을 가려내기 위함
     from (
          select region
               , create_year_month
               , count(distinct user_id) as user_cnt
          from registere_user
          group by region, create_year_month
          having create_year_month >= '2022-05'
     ) as a
     order by region, create_year_month
  )

  select region, create_year_month
       , rank_asc
       , user_cnt
       , bef_1m_user_cnt
       -- 각 지역별 11월 NRU의 전월대비 증감률을 계산하고, 이를 통해 유저 그룹을 나눈다.
       , (user_cnt - bef_1m_user_cnt)/bef_1m_user_cnt as rate_of_change
       , last_value((user_cnt - bef_1m_user_cnt)/bef_1m_user_cnt) over(partition by region order by create_year_month rows between unbounded preceding and unbounded following) as nov_rate_of_change
       , case when rank_asc = 1 and create_year_month = '2022-11' then 'new'
              when last_value((user_cnt - bef_1m_user_cnt)/bef_1m_user_cnt) over(partition by region order by create_year_month rows between unbounded preceding and unbounded following) < 0 then 'decrease'
              when last_value((user_cnt - bef_1m_user_cnt)/bef_1m_user_cnt) over(partition by region order by create_year_month rows between unbounded preceding and unbounded following) between 0 and 0.1 then 'increase_0_10'
              when last_value((user_cnt - bef_1m_user_cnt)/bef_1m_user_cnt) over(partition by region order by create_year_month rows between unbounded preceding and unbounded following) <= 0.2 then 'increase_10_20'
              when last_value((user_cnt - bef_1m_user_cnt)/bef_1m_user_cnt) over(partition by region order by create_year_month rows between unbounded preceding and unbounded following) <= 0.3 then 'increase_20_30'
              else 'increase_30_more'
         end as user_group
  from montly_registere_user
  order by region, create_year_month
""")
monthlyNruByRegionDf = query_job.to_dataframe()



##---< 시각화 편의를 위한 데이터프레임 병합 & 컬럼명 변경 & 값 변경 >-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------


## < monthlyAuAndNru: 월간 지역별 활성 유저수, 가입 유저수 >

mauByRegionDf = mauByRegionDf.rename(columns={'login_year_month':'year_month'})
mauByRegionDf['category'] = 'AU'
monthlyNruByRegionDf = monthlyNruByRegionDf.rename(columns={'create_year_month':'year_month'})
monthlyNruByRegionDf['category'] = 'NRU'
monthlyAuAndNru = pd.concat([mauByRegionDf, monthlyNruByRegionDf], ignore_index=True) 

# user_group 한글로 변경
monthlyAuAndNru['user_group'] = np.where(monthlyAuAndNru['user_group'] == 'new', '신규지역', monthlyAuAndNru['user_group'])
monthlyAuAndNru['user_group'] = np.where(monthlyAuAndNru['user_group'] == 'decrease', '감소지역', monthlyAuAndNru['user_group'])
monthlyAuAndNru['user_group'] = np.where(monthlyAuAndNru['user_group'] == 'increase_0_10', '10%이하_증가지역', monthlyAuAndNru['user_group'])
monthlyAuAndNru['user_group'] = np.where(monthlyAuAndNru['user_group'] == 'increase_10_20', '10%초과_20%이하_증가지역', monthlyAuAndNru['user_group'])
monthlyAuAndNru['user_group'] = np.where(monthlyAuAndNru['user_group'] == 'increase_20_30', '20%초과_30%이하_증가지역', monthlyAuAndNru['user_group'])
monthlyAuAndNru['user_group'] = np.where(monthlyAuAndNru['user_group'] == 'increase_30_more', '30%_초과_증가지역', monthlyAuAndNru['user_group'])


In [ ]:
#@title Visualization-2 ⛳️

## << 지역별 AU, NRU >>

import plotly.express as px

## Step.1 - fig에 px.line() 그래프 담기
fig = px.line(monthlyAuAndNru, 
              x="year_month", 
              y= "user_cnt", 
              color="region",
              facet_col = "user_group",
              facet_row = "category",
              # facet_row_spacing = 0.05, #  (float between 0 and 1) – Spacing between facet rows, in paper units. Default is 0.03 or 0.07 when facet_col_wrap is used.
              markers=True,
              category_orders={"user_group": ["신규지역", "감소지역", "10%이하_증가지역", "30%_초과_증가지역"]}, # '10%초과_20%이하_증가지역', '20%초과_30%이하_증가지역' 은 데이터가 없어서 제외
              hover_data={"category":False, "user_group":False}
              )

## Step.2 - fig의 layout 설정 변경
fig.update_layout(
    {
        "title": {
            "text": "<b>< 월간 지역별 MAU, NRU 추이 비교 ><b>",
            "x": 0.5,
            "y": 0.99,
            "font": {
                "size": 15
            }
        },
        "yaxis1": {
            "title": "NRU(명)",
            "tickformat": ","
        },
        "yaxis5": {
            "title": "MAU(명)",
            "tickformat": ","
        },
        "legend_traceorder": "normal", #normal(default - 데이터 순서대로), reversed(역순)
        "legend_title_text": "거주 지역"
    },
    height = 550 
)

## Step.3 - fig의 x축 상세 설정
fig.update_xaxes(showticklabels=True) # 1행, 2행 모두 x축 thick 출력
fig.update_xaxes(tickformat = '%m월', dtick = "M1", tick0 = "2022-05", title = "")

## Step.4 - 그래프 마우스 오버시 hovermode x축으로 설정
fig.update_layout(hovermode="x")

## Step.5 - 그래프 출력
fig.show()

> **Note**

- user_group 분류기준: 11월 지표의 전월比 증감률을 기준으로 계산

> **Comment**

- 11월 MAU의 경우 문래동3가 지역을 제외한 모든 지역이 전월比 상승
  - 30% 초과 증가지역은 모두 신규 모객 유저를 통한 증가이며 (MAU중 NRU가 차지하는 비중이 평균 82.1% 수준)
  - 10% 이하 증가지역인 목동과 신도림동의 경우 신규 유입이 전월比 각각 13%, 40% 감소했지만 기존 유저들의 재방문으로 인해 MAU 상승

## < 가입 연도별/월별 MAU >



In [ ]:
#@title Make DataFrame-1

## << yearlyAuDf: 가입 연도별 활성 유저수 >>
query_job = client.query("""
  with active_user as (
    select a.login_date, a.login_year_month, b.create_date, format_date("%Y", b.create_date) as create_year, a.user_id, b.region_1depth_name, b.region_2depth_name, region_3depth_name
    from `crypto-song-379002.my_temp.daily_login_users` as a
    inner join `crypto-song-379002.my_temp.my_infos` as b
    on a.user_id = b.user_id
  )

  select login_year_month, create_year 
       , count(distinct user_id) as user_cnt
  from active_user
  group by login_year_month, create_year
  order by login_year_month, create_year
""")
yearlyAuDf = query_job.to_dataframe()

In [ ]:
#@title Visualization-1

## << 가입 연도별 월간 활성 유저수 - Bar Chart >>

import plotly.express as px

## Step.1 - fig에 px.bar() 그래프 담기
fig = px.bar(yearlyAuDf, 
              x="login_year_month", 
              y="user_cnt", 
              color="create_year", 
              text="user_cnt",
             )

## Step.2 - text 표현 형식과, 출력 위치를 조정
fig.update_traces(texttemplate='%{text:,}명', textposition='inside') 

## Step.3 - fig의 layout 설정 변경
fig.update_layout(
    {
        "title": {
            "text": "<b>< 가입 연도별 MAU ><b>",
            "x": 0.5,
            "y": 0.95,
            "font": {
                "size": 13
            }
        },
        "yaxis": { "title": "MAU", "tickformat": ','  }, 
        "xaxis": {
            "title": "",
            "tick0": "2022-05",
            "dtick": 'M1',
            "tickformat": "%Y-%m"
        },
        "legend_title_text": "가입 연도",
        "template":'plotly_white',
    }
)

## Step.4 - fig의 y축을 기준으로, 직사각형 영역 표시 또는 텍스트를 남깁니다.
fig.add_vrect(x0="2022-07-17", 
              x1="2022-10-16",
              annotation_text="* 2022년 가입유저 기준, 유입보다 이탈 속도가 빠른 구간", 
              annotation_position="top left",
              # annotation_font_size=14,
              fillcolor="hotpink", opacity=0.25, line_width=0)

fig.add_vrect(x0="2022-10-18", 
              x1="2022-11-15",
              annotation_text="* 신규 매장 오픈", 
              annotation_position="top left",
              # annotation_font_size=14,
              fillcolor="skyblue", opacity=0.25, line_width=0)

## Step.5 - 그래프 출력
fig.show()

> **Comment**

- 2022년 가입 그룹의 MAU는 7월 이후 10월까지 하락세로 전환됨 (매달 500명 이상의 신규가입자가 발생하고 있으나 유저의 이탈 속도가 더 빠름)
- 2022년 가입 그룹의 11월 MAU는 신규매장 오픈 & 다판다마켓 인수에 따라 역대 최고 수준(5,042명) 달성


In [ ]:
#@title Make DataFrame-2

## << monthlyAuDf: 가입 연월별 활성 유저수 >>
query_job = client.query("""
  with active_user as (
    select a.login_date, a.login_year_month, b.create_date, create_year_month, a.user_id, b.region_1depth_name, b.region_2depth_name, region_3depth_name
    from `crypto-song-379002.my_temp.daily_login_users` as a
    inner join `crypto-song-379002.my_temp.my_infos` as b
    on a.user_id = b.user_id
  )

  select login_year_month, create_year_month, substr(create_year_month, 1, 4) as create_year 
       , count(distinct user_id) as user_cnt
  from active_user
  group by login_year_month, create_year_month
  order by login_year_month, create_year_month
""")
monthlyAuDf = query_job.to_dataframe()

In [ ]:
#@title Visualization-2

## << 가입 연월별 월간 활성 유저수 - Bar Chart >>

import plotly.express as px

## Step.1 - fig에 px.bar() 그래프 담기
fig = px.line(monthlyAuDf, 
              x="login_year_month", 
              y="user_cnt", 
              color="create_year_month", 
              # text="user_cnt",
              markers=True,
              hover_data = {"create_year":False, "login_year_month":False,}, # 마우스 오버시 노출하고 싶지 않은 데이터 제외 처리
              facet_col="create_year",
              facet_col_spacing = 0.05,
             )

## Step.2 - text 표현 형식과, 출력 위치를 조정
fig.update_traces(texttemplate='%{text:,}명') 

## Step.3 - fig의 layout 설정 변경
fig.update_layout(
    {
        "title": {
            "text": "<b>< 가입 연월별 MAU ><b>",
            "x": 0.5,
            "y": 0.95,
            "font": {
                "size": 13
            }
        },
        "yaxis": { "title": "MAU", "tickformat": ','  }, 
        "yaxis2": { "title": "", "tickformat": ','  }, 
        "xaxis": {
            "title": "",
            "tick0": "2022-05",
            "dtick": 'M1',
            "tickformat": "%Y-%m"
        },
        "xaxis2": {
            "title": "",
            "tick0": "2022-05",
            "dtick": 'M1',
            "tickformat": "%Y-%m"
        },
        "legend_title_text": "가입 연월",
        # "template":'plotly_white',
        "height": 500
    }
)

## Step.4 - fig의 y축 상세 설정
fig.update_yaxes(matches=None, showticklabels=True) # matches=None (y축을 독립적으로 설정)

## Step.5 - fig의 y축을 기준으로, 직사각형 영역 표시 또는 텍스트를 남깁니다.
fig.add_vrect(x0="2022-10-16", 
              x1="2022-11-15",
              # y0=0,
              # y1=0.4,
              annotation_text="* MAU 일시적 반등 구간", 
              annotation_position="right top",
              fillcolor="hotpink", opacity=0.15, line_width=0,
              col=1) # https://plotly.com/python/horizontal-vertical-shapes/#horizontal-and-vertical-lines-in-dash 

fig.add_vrect(x0="2022-10-16", 
              x1="2022-11-15",
              # y0=0,
              # y1=0.4,
              annotation_text="* MAU 감소율 일시적 방어 구간", 
              annotation_position="right top",
              fillcolor="crimson", opacity=0.15, line_width=0,
              col=2) # https://plotly.com/python/horizontal-vertical-shapes/#horizontal-and-vertical-lines-in-dash 


## Step.6 - 그래프 마우스 오버시 hovermode x축으로 설정
fig.update_layout(hovermode="x")

## Step.6 - 그래프 출력
fig.show()

> **Comment**

- 그룹별 MAU 증감 추이를 살펴봤을때 신규매장 오픈 이슈가 없었다면 11월 MAU는 10월 보다 낮거나 비슷한 수준이 유지되었을 것으로 추정됨
- 11월 신규매장 오픈 및 다판다마켓 인수는 어떻게 기존 유저들의 MAU 감소를 방어에 영향을 주었는지 확인 필요

In [ ]:
#@title Make DataFrame-3 ⛳️

## << auChurnedRateDf: 가입 연월별 - 최초 유입시점 볼륨 대비 미접속률 >>
query_job = client.query("""

  -- 일간 접속유저 테이블(+ 거주지역, 가입시점) 
  with active_user as (
    select a.login_date, a.login_year_month, b.create_date, b.create_year_month, a.user_id, b.region_1depth_name, b.region_2depth_name, region_3depth_name
    from `crypto-song-379002.my_temp.daily_login_users` as a
    inner join `crypto-song-379002.my_temp.my_infos` as b
    on a.user_id = b.user_id
  ),

  -- 가입월별, 접속월별 접속 유저수 & 가입시점 기준 최초 접속 유저수 테이블
  active_user_by_create_month as (
     select login_year_month, create_year_month, user_cnt
          , first_value(user_cnt) over(partition by create_year_month order by login_year_month) as first_user_cnt -- 가입 시점 기준 최초 접속 유저수
     from (
          select login_year_month, create_year_month 
               , count(distinct user_id) as user_cnt
          from active_user
          group by login_year_month, create_year_month
     ) as a
     order by create_year_month, login_year_month
  )

  select login_year_month, create_year_month
       , substr(create_year_month, 1, 4) as create_year
       , concat('M+', rank() over(partition by create_year_month order by login_year_month) - 1) as time_order
       , user_cnt
       , first_user_cnt
       , round(user_cnt/first_user_cnt, 4) as rate_of_change
  from active_user_by_create_month 
""")
auChurnedRateDf = query_job.to_dataframe()
auChurnedRateDf = auChurnedRateDf.rename(columns={"first_user_cnt":"M+0_user_count"})



##---< 시각화 편의를 위한 데이터프레임 형태 변경 >-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

## << auChurnedCntAndRateDf: 가입 연월별 - 월간(접속 유저수, 재접속률) - M+0부터 추적 가능한 2022-05 유입 유저부터 잘라냄 >>
auChurnedCntAndRateDf = auChurnedRateDf[auChurnedRateDf['create_year_month'] >= '2022-05']\
.sort_values(by=["create_year_month", "login_year_month"])\
.melt(id_vars=["create_year_month", "login_year_month", "create_year", "time_order"], value_vars=["user_cnt", "rate_of_change"]) 

In [ ]:
#@title Visualization-3 ⛳️

## << 가입연월별 최초유입시점대비 재접속률 변화 >>
import plotly.express as px

## Step.1 - fig에 px.line() 그래프 담기
fig = px.line(auChurnedCntAndRateDf, 
              x="time_order", 
              y="value", 
              color="create_year_month",
              facet_col = "variable",
              facet_col_spacing = 0.07, #  (float between 0 and 1) – Spacing between facet rows, in paper units. Default is 0.03 or 0.0.7 when facet_col_wrap is used.
              markers=True,
              category_orders={"create_year_month": ["2021-07", "2021-08", "2021-09", "2021-10", "2021-11", "2021-12", 
                                                     "2022-01", "2022-02", "2022-03", "2022-04", "2022-05", "2022-06", "2022-07", "2022-08", "2022-09", "2022-10", "2022-11", "2022-12"]},
              hover_data = {"variable":False, "time_order": False} # 마우스 오버시 노출하고 싶지 않은 데이터 제외 처리
              )

## Step.2 - fig의 layout 설정 변경
fig.update_layout(
    {
        "title": {
            "text": "<b>< 가입 연월별 AU의 M+n 재접속률 ><b>",
            "x": 0.5,
            "y": 0.99,
            "font": {
                "size": 13
            }
        },
        "xaxis": {
            "title": "",
            "tick0": "1",
        },
        "xaxis2": {
            "title": "",
            "tick0": "1",
        },
        "legend_traceorder": "normal", #normal(default - 데이터 순서대로), reversed(역순)
        "legend_title_text": "가입 연월"
    },
    height = 350 
)


## Step.3 - fig의 화살표 설정
fig.add_annotation(
  x="M+1",  # arrows' head
  y=0.4,  # arrows' head
  ax="M+1",  # arrows' tail
  ay=0.6,  # arrows' tail
  xref='x2',
  yref='y2',
  axref='x2',
  ayref='y2',
  text='점진적 하락세',  # if you want only the arrow: ''
  font=dict(size=14, color='black'), showarrow=True,
  arrowhead=3,
  arrowsize=1,
  arrowwidth=2,
  arrowcolor='hotpink',
  row=1, col=2
)

## Step.4 - fig의 y축을 기준으로, 직사각형 영역 표시 또는 텍스트를 남깁니다.
fig.add_vrect(x0="M+0", 
              x1="M+2",
              annotation_text="", 
              # annotation_position="top left",
              fillcolor="hotpink", opacity=0.15, line_width=0) # https://plotly.com/python/horizontal-vertical-shapes/#horizontal-and-vertical-lines-in-dash 

## Step.5 - fig의 y축 상세 설정
fig.update_yaxes(title='활성 유저수(명)', row=1, col=1)
fig.update_yaxes(tickformat = ',', row=1, col=1)
fig.update_yaxes(title='재접속률(%)', row=1, col=2)
fig.update_yaxes(tickformat = '.0%', row=1, col=2)
fig.update_yaxes(matches=None, showticklabels=True) # matches=None (y축을 독립적으로 설정)

## Step.6 - 그래프 마우스 오버시 hovermode x축으로 설정
fig.update_layout(hovermode="x")

## Step.7 - 그래프 출력
fig.show()

> **Comment**

- **22년 후반으로 갈수록 모객 집단의 이탈률이 가속화 되고 있는 것으로 추정**
  - **관련 근거 1)** 22년 5월부터 10월까지(8월 제외) 각 그룹별 M+1 재접속률이 지속적으로 하락
  - **관련 근거 2)** 22년 10월 보다 모수가 200명 이상 큰 7월, 6월의 M+1 재접속률은 10월比 약 11%p 높은 48% 수준 
- **이탈률 가속 현상이 특정 지역의 이슈인지 확인 필요**
  - 아래의 < 가입 연월별 지역별 AU의 M+1 재접속률 비교 > 참고


## < 가입 월별 지역별 M+1 재접속률 >

In [ ]:
#@title Make DataFrame 

## << auChurnedRateByRegionDf: 가입 연월별 지역별 - 최초 유입시점 볼륨 대비 미접속률 >>
query_job = client.query("""

  -- 일간 접속유저 테이블(+ 거주지역, 가입시점) 
  with active_user as (
    select a.login_date, a.login_year_month, b.create_date, b.create_year_month, a.user_id, b.region_1depth_name, b.region_2depth_name, region_3depth_name
    from `crypto-song-379002.my_temp.daily_login_users` as a
    inner join `crypto-song-379002.my_temp.my_infos` as b
    on a.user_id = b.user_id
  ),

  -- 가입월별, 접속월별, 지역별 접속 유저수 & 가입시점 기준 최초 접속 유저수 테이블
  active_user_by_create_month as (
     select login_year_month, create_year_month, region, user_cnt
          , first_value(user_cnt) over(partition by create_year_month, region order by login_year_month) as first_user_cnt
     from (
          select login_year_month, create_year_month, region_3depth_name as region 
               , count(distinct user_id) as user_cnt
          from active_user
          group by login_year_month, create_year_month, region
     ) as a
     order by create_year_month, login_year_month, region
  )

  select login_year_month, create_year_month, substr(create_year_month, 1, 4) as create_year, region
       , concat('M+', dense_rank() over(partition by create_year_month order by login_year_month) - 1) as time_order
       , user_cnt, first_user_cnt, round(user_cnt/first_user_cnt, 4) as rate_of_change
  from active_user_by_create_month 
""")
auChurnedRateByRegionDf = query_job.to_dataframe()
auChurnedRateByRegionDf = auChurnedRateByRegionDf.rename(columns={"first_user_cnt":"M+0_user_count"})


##---< 시각화 편의를 위한 데이터프레임 형태 변경 >-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

# << auChurnedCntAndRateDf: 가입 연월별 지역별 - 월간(접속 유저수, 재접속률) - M+0부터 추적 가능한 2022-05 유입 유저부터 잘라냄 >>
auChurnedCntAndRateByRegionDf = auChurnedRateByRegionDf[auChurnedRateByRegionDf['create_year_month'] >= '2022-05']\
.sort_values(by=["create_year_month", "login_year_month", "region"])\
.melt(id_vars=["create_year_month", "login_year_month", "create_year", "region", "time_order"], value_vars=["user_cnt", "rate_of_change"]) 

In [ ]:
#@title Visualization-1 

## << 가입연월별 최초유입시점 대비 M+1 재접속률 변화 >>
import plotly.express as px

## Step.1 - fig에 px.line() 그래프 담기
fig = px.line(auChurnedCntAndRateByRegionDf[(auChurnedCntAndRateByRegionDf['create_year_month'] <= '2022-10') &
                                            (auChurnedCntAndRateByRegionDf['create_year_month'] >= '2022-05') & 
                                            (auChurnedCntAndRateByRegionDf['time_order'].str.contains("0|1"))].rename(columns = {"create_year_month": "가입연월"}), # 비교에 필요한 부분만 잘라내는 과정
              x="time_order", 
              y="value", 
              color="region",
              facet_col = "가입연월",
              # facet_col_spacing = 0.05, #  (float between 0 and 1) – Spacing between facet rows, in paper units. Default is 0.03 or 0.0.7 when facet_col_wrap is used.
              facet_row = "variable",
              markers=True,
              category_orders={"가입연월": ["2022-05", "2022-06", "2022-07", "2022-08", "2022-09", "2022-10"],
                               "time_order": ["M+0", "M+1"]},
              )

## Step.2 - fig의 layout 설정 변경
fig.update_layout(
    {
        "title": {
            "text": "<b>< 가입 연월별 지역별 MAU의 M+1 재접속률 비교 ><b>",
            "x": 0.5,
            "y": 0.99,
            "font": {
                "size": 15
            }
        },
        "legend_traceorder": "normal", #normal(default - 데이터 순서대로), reversed(역순)
        "legend_title_text": "거주 지역"
    },
)

## Step.3 - fig의 y축을 기준으로, 직사각형 영역 표시 또는 텍스트를 남깁니다.
fig.add_vrect(x0="M+0", 
              x1="M+1",
              y0=0,
              y1=0.4,
              annotation_text="* 재접속률 0 ~ 50% 구간", 
              annotation_position="bottom left",
              fillcolor="hotpink", opacity=0.15, line_width=0,
              row=1) # https://plotly.com/python/horizontal-vertical-shapes/#horizontal-and-vertical-lines-in-dash 


## Step.4 - fig의 x축 또는 y축 상세 설정
fig.update_xaxes(title='', row=1)

fig.update_yaxes(title='MAU(명)', row=2, col=1)
fig.update_yaxes(tickformat = ',', row=2)
fig.update_yaxes(range=[-100, 700], row=2)

fig.update_yaxes(title='재접속률(%)', row=1, col=1)
fig.update_yaxes(tickformat = '.0%', row=1)
fig.update_yaxes(tickformat = '.0%', row=1)
fig.update_yaxes(matches=None, showticklabels=True)
fig.update_yaxes(range=[0, 1.2], row=1)

## Step.5 - 그래프 출력
fig.show()

# **[ 잔존율 분석 ]**

## < 요약 ✨ >

> **유저 타입별 잔존율**
  - 다판다마켓 유저들이 대거 유입되면서, 신규 유저의 11월 일평균 D+1 잔존율이 일시적으로 상승 (전월比 40.8%p 상승한 69.4%)
  - 신규유저를 제외한 11월 재방문 유저의 일평균 D+1 잔존율이 64.5%로 전월比 3.8%p 상승한 것으로 보아 
  - 다판다마켓의 공급 상품이 기존 유저들의 재접속률을 견인한게 아닌지 확인 필요  
  
> **지역별 잔존율**
  - 다판다마켓 실 수요 지역의 잔존율이 기존의 판매지역인 목동점보다 높게 집계됨
  - 이러한 추세가 유지될 경우, 두 업체간 판매전략 차이 분석을 통해 로컬팜 전체 매출을 추가 상승 시킬 수 있는 방안 도출 필요 

## < 신규 유저 잔존율 현황 >

In [ ]:
#@title Make DataFrame

## << monthlyAvgNdayRetByNRU: 유저 타입별 월간 일평균 D+day 잔존율 >>
query_job = client.query("""

    -- 월별/일별 신규가입 유저 목록 테이블
    with monthly_new_user_list as (
        select create_year_month
             , create_date
             , user_id
        FROM `my_temp.my_infos`
    ), 

    -- 일간 유저별 접속 로그 테이블
    daily_login as (
        select distinct login_date
             , login_year_month
             , user_id
        from `my_temp.daily_login_users`
    ),

    -- [신규유저] 일간 접속유저 D+1/7/14/30 N-day 접속여부 확인 테이블
    d_plus_day_check_login as (
        select distinct a.login_date, a.login_year_month
             , date_diff(CAST('2022-11-30' AS DATE), a.login_date, DAY) as date_diff_count -- 추적 기간이 다 차지 않은 경우 예외처리 해주기 위한 컬럼
             , a.user_id
             , case when d1.user_id is not null then 1 end as d1_login
             , case when d7.user_id is not null then 1 end as d7_login
             , case when d14.user_id is not null then 1 end as d14_login
             , case when d30.user_id is not null then 1 end as d30_login
        from (
          select distinct a.login_date, a.login_year_month, a.user_id
          from daily_login as a
          where exists ( 
            -- 신규유저만 추려내는 작업
            select 1
            from monthly_new_user_list as b
            where a.user_id = b.user_id and a.login_date = b.create_date
          )
        ) as a 
        left join (
          select login_date, user_id 
          from daily_login
        ) as d1
        on a.user_id = d1.user_id and date_add(a.login_date, interval 1 day) = d1.login_date
        left join (
          select login_date, user_id 
          from daily_login
        ) as d7
        on a.user_id = d7.user_id and date_add(a.login_date, interval 7 day) = d7.login_date
        left join (
          select login_date, user_id 
          from daily_login
        ) as d14
        on a.user_id = d14.user_id and date_add(a.login_date, interval 14 day) = d14.login_date
        left join (
          select login_date, user_id 
          from daily_login
        ) as d30
        on a.user_id = d30.user_id and date_add(a.login_date, interval 30 day) = d30.login_date
        order by a.login_date, a.user_id
    )

    -- 신규유저 월간 접속유저 일평균 N-day 잔존율 집계
    select login_year_month
         , '신규유저' as user_type
         , count(distinct user_id) as mau
         , count(user_id) as mau_not_unique -- mau와 mau_not_unique가 같다.(신규유저의 경우 가입일(=최초 접속일)에 대해서만 추적 집계되기 때문)
         , round(sum(case when date_diff_count >= 1 then d1_login end) / count(distinct case when date_diff_count >= 1 then user_id end), 3) as d1_ret
         , round(sum(case when date_diff_count >= 7 then d7_login end) / count(distinct case when date_diff_count >= 7 then user_id end), 3) as d7_ret
         , round(sum(case when date_diff_count >= 14 then d14_login end) / count(distinct case when date_diff_count >= 14 then user_id end), 3) as d14_ret
         , round(sum(case when date_diff_count >= 30 then d30_login end) / count(distinct case when date_diff_count >= 30 then user_id end), 3) as d30_ret
    from d_plus_day_check_login
    group by login_year_month, user_type
    order by login_year_month, user_type
""")

monthlyAvgNdayRetByNRU = query_job.to_dataframe()


##------------------------------------------------------------------------------------------------------------------------------------------------------------##


## << dailyNdayRetByNRU: 유저 타입별 일간 D+day 잔존율 >>
query_job = client.query("""

    -- 월별/일별 신규가입 유저 목록 테이블 (상동)
    with monthly_new_user_list as (
        select create_year_month
             , create_date
             , user_id
        FROM `my_temp.my_infos`
    ), 

    -- 일간 유저별 접속 로그 테이블 (상동)
    daily_login as (
        select distinct login_date
             , login_year_month
             , user_id
        from `my_temp.daily_login_users`
    ),

    -- [신규유저] 일간 접속유저 D+1/7/14/30 N-day 접속여부 확인 테이블 (상동)
    d_plus_day_check_login as (
        select distinct a.login_date, a.login_year_month
             , date_diff(CAST('2022-11-30' AS DATE), a.login_date, DAY) as date_diff_count -- 추적 기간이 다 차지 않은 경우 예외처리 해주기 위한 컬럼
             , a.user_id
             , case when d1.user_id is not null then 1 end as d1_login
             , case when d7.user_id is not null then 1 end as d7_login
             , case when d14.user_id is not null then 1 end as d14_login
             , case when d30.user_id is not null then 1 end as d30_login
        from (
          select distinct a.login_date, a.login_year_month, a.user_id
          from daily_login as a
          where exists ( 
            -- 신규유저만 추려내는 작업
            select 1
            from monthly_new_user_list as b
            where a.user_id = b.user_id and a.login_date = b.create_date
          )
        ) as a 
        left join (
          select login_date, user_id 
          from daily_login
        ) as d1
        on a.user_id = d1.user_id and date_add(a.login_date, interval 1 day) = d1.login_date
        left join (
          select login_date, user_id 
          from daily_login
        ) as d7
        on a.user_id = d7.user_id and date_add(a.login_date, interval 7 day) = d7.login_date
        left join (
          select login_date, user_id 
          from daily_login
        ) as d14
        on a.user_id = d14.user_id and date_add(a.login_date, interval 14 day) = d14.login_date
        left join (
          select login_date, user_id 
          from daily_login
        ) as d30
        on a.user_id = d30.user_id and date_add(a.login_date, interval 30 day) = d30.login_date
        order by a.login_date, a.user_id
    )


    -- 신규유저 일간 접속유저 N-day 잔존율 집계
    select login_date
         , '신규유저' as user_type
         , count(distinct user_id) as dau
         , count(user_id) as dau_not_unique
         , round(sum(d1_login)/count(user_id), 3) as d1_ret
         , round(sum(d7_login)/count(user_id), 3) as d7_ret
         , round(sum(d14_login)/count(user_id), 3) as d14_ret
         , round(sum(d30_login)/count(user_id), 3) as d30_ret
    from d_plus_day_check_login
    group by login_date, user_type
    order by login_date, user_type
""")

dailyNdayRetByNRU = query_job.to_dataframe()

In [ ]:
#@title Visualization-1 

## << 신규 유저 월간 일평균 N-day 잔존율 >>

import plotly.express as px
from plotly.subplots import make_subplots

# step.1 - 서브플랏 선언(이중축)
subfig = make_subplots(specs=[[{"secondary_y": True}]])

# step.2 - fig1(잔존율 그래프) 생성
fig1 = px.line(monthlyAvgNdayRetByNRU, 
              x="login_year_month", 
              y=['d1_ret', 'd7_ret', 'd14_ret', 'd30_ret'],
              line_group="variable", 
              text="value",
              markers=True,
             )

fig1.update_traces(
    yaxis="y2",
    textposition='top center',
    texttemplate='%{text: .1%}',
    hovertemplate = '%{y:.1%}',
)

# step.4 - fig2(mau 그래프) 생성
fig2 = px.bar(monthlyAvgNdayRetByNRU, 
             x="login_year_month", 
             y="mau", 
            )
fig2.update_traces(marker_color='lightgray')  # e.g. red, hotpink, blue, skyblue, ...

# step.5 - subfig에 fig1, fig2를 통합 할당
subfig.add_traces(fig1.data + fig2.data)
subfig.update_layout(
    {
        "title": {
            "text": "<b>< 신규 유저 월간 일평균 N-day 잔존율 ><b>",
            "x": 0.5,
            "y": 0.9,
            "font": {
                "size": 13
            }
        },
        "xaxis": {
            "title": "",
            "tick0": "2022-05-01",
            "dtick": 'M1',
            "tickformat": "%m월"
        },
        "yaxis": { "title": "MAU(명)", "tickformat": ',' },
        "yaxis2": { "title": "Avg. N-day Retention(%)", "tickformat": '.1%', "range": [0, 0.8]},
        "legend_title_text": "N-day 잔존율",
        "template":'plotly_white',
    }
)

subfig.update_layout(hovermode="x")

# step.6 - secondary_y 축의 gird 만 보이게 하기
subfig['layout']['yaxis1']['showgrid'] = False

# step.7 - 그래프 출력
subfig.show()

> **Note**

- 11월 잔존율의 경우 집계 가능한 모수로 한정하여 평균값이 계산됨 (예를들어 D+14 잔존율은 (11/1~11/16) 접속유저에 대한 D+14 잔존율 평균값을 제공)
- 따라서 11월 D+7 ~ D+14 일평균 잔존율의 경우 전체 모수에 대한 집계값이 아니므로 참고용으로만 사용

> **Comment**

- 8월 부터 10월까지 신규유저의 월간 일평균 잔존율은 지속 하락세 였으나
- 다판다마켓의 기존고객 유입으로 인해 11월 D+1 잔존율이 전월比 40.8%p 상승한 69.4% 달성

In [ ]:
#@title Visualization-2

## << 신규 유저 월간 일평균 N-day 잔존율 >>

import plotly.express as px
from plotly.subplots import make_subplots

# step.2 - 서브플랏 할당
subfig = make_subplots(specs=[[{"secondary_y": True}]])

# step.3 - fig1(잔존율 그래프) 생성
fig1 = px.line(dailyNdayRetByNRU, 
              x="login_date", 
              y=['d1_ret', 'd7_ret', 'd14_ret', 'd30_ret'],
              color="variable", 
             )
fig1.update_traces(yaxis="y2") # fig1의 y축을 보조축으로 변환

# step.4 - fig2(dau 그래프) 생성
fig2 = px.bar(dailyNdayRetByNRU, 
             x="login_date", 
             y="dau", 
            )
fig2.update_traces(marker_color='lightgray')

# step.5 - subfig에 fig1, fig2를 통합 할당
subfig.add_traces(fig1.data + fig2.data)
subfig.update_layout(
    {
        "title": {
            "text": "<b>< 신규 유저 N-day 잔존율 ><b>",
            "x": 0.5,
            "y": 0.8,
            "font": {
                "size": 13
            }
        },
        "xaxis1": {
            "title": "",
            "tick0": "2022-05-01",
            "dtick": 'M1',
            "tickformat": "%Y-%m-%d"
        },
        "yaxis": { "title": "DAU(명)", "tickformat": ',', "range": [0, 1000] },
        "yaxis2": { "title": "N-day Retention(%)", "tickformat": '.0%', "range": [0, 1]},
        "legend_title_text": "N-day 잔존율",
        "template":'plotly_white',
    }
)

# step.6 - 잔존율 탐색 기준선 도식
subfig.add_hline(y=0.7, 
                 line_dash="dot", 
                 secondary_y=True,
                 )
# step.6 - 잔존율 탐색 기준선 관련 내용 표기
subfig.add_annotation(
    x='2022-11-07',
    y=700,
    xref="x",
    yref="y",
    text="잔존율 70% 기준선",
    showarrow=True,
    font=dict(
        size=12,
        color="Gray"
    ),
    align="right",
    arrowhead=2,
    ax=-60,
    ay=-30
)


# step.7 - 신규 매장 입점 기간 표시
subfig.add_vrect(x0="2022-06-13", 
                 x1="2022-06-16",
                 annotation_text="* 신규 매장 입점(6/14 ~ 6/15)", 
                 annotation_position="top left",
                 fillcolor="skyblue", opacity=0.25, line_width=0)

subfig.add_vrect(x0="2022-11-06", 
                 x1="2022-11-09",
                 annotation_text="* 신규 매장 입점(11/7 ~ 11/8)", 
                 annotation_position="top right",
                 fillcolor="skyblue", opacity=0.25, line_width=0)

subfig.add_vrect(x0="2022-11-21", 
                 x1="2022-11-30",
                 annotation_text="* 11월 3주차 ~", 
                 annotation_position="top right",
                 fillcolor="hotpink", opacity=0.25, line_width=0)

# step.8 - secondary_y 축의 gird 만 보이게 하기
subfig['layout']['yaxis1']['showgrid'] = False

# step.9 - 그래프 출력
subfig.show()

> **Comment**

- 앞서 살펴본 11월 일평균 D+1 잔존율의 급상승은 2주차에 발생한 다판다마켓 유저 대량유입에 기인하며
- 11월 3주차 부터 잔존율 퍼포먼스가 이전 수준으로 회귀하는것으로 보아 12월에는 다시 10월 수준으로 회귀할것으로 예상됨

## < 재방문 유저 잔존율 현황 >

In [ ]:
#@title Make DataFrame ⛳️

## << monthlyAvgNdayRetByRVU: 유저 타입별 월간 일평균 D+day 잔존율 >>
query_job = client.query("""

    -- 월별/일별 신규가입 유저 목록 테이블
    with monthly_new_user_list as (
        select create_year_month
             , create_date
             , user_id
        FROM `my_temp.my_infos`
    ), 

    -- 일간 유저별 접속 로그 테이블
    daily_login as (
        select distinct login_date
             , login_year_month
             , user_id
        from `my_temp.daily_login_users`
    ),

    -- [재방문유저] 일간 접속유저 D+1/7/14/30 N-day 접속여부 확인 테이블
    d_plus_day_check_login as (
        select distinct a.login_date, a.login_year_month
             , date_diff(CAST('2022-11-30' AS DATE), a.login_date, DAY) as date_diff_count -- 추적 기간이 다 차지 않은 경우 예외처리 해주기 위한 컬럼
             , a.user_id
             , case when d1.user_id is not null then 1 end as d1_login
             , case when d7.user_id is not null then 1 end as d7_login
             , case when d14.user_id is not null then 1 end as d14_login
             , case when d30.user_id is not null then 1 end as d30_login
        from (
          select distinct a.login_date, a.login_year_month, a.user_id
          from daily_login as a
          where not exists ( -- 신규유저 골라낼때와는 다르게, not exists 로 되어있음!
            -- 재방문 유저만 추려내는 작업(신규유저는 유입된 월 동안 재방문 유저에서 제외 - e.g, 2/14일 가입한 신규유저는 2월당 내내 신규유저로 분류) 
            select 1
            from monthly_new_user_list as b
            where a.user_id = b.user_id and a.login_year_month = b.create_year_month
          )
        ) as a 
        left join (
          select login_date, user_id 
          from daily_login
        ) as d1
        on a.user_id = d1.user_id and date_add(a.login_date, interval 1 day) = d1.login_date
        left join (
          select login_date, user_id 
          from daily_login
        ) as d7
        on a.user_id = d7.user_id and date_add(a.login_date, interval 7 day) = d7.login_date
        left join (
          select login_date, user_id 
          from daily_login
        ) as d14
        on a.user_id = d14.user_id and date_add(a.login_date, interval 14 day) = d14.login_date
        left join (
          select login_date, user_id 
          from daily_login
        ) as d30
        on a.user_id = d30.user_id and date_add(a.login_date, interval 30 day) = d30.login_date
        order by a.login_date, a.user_id
    )

    -- 재방문유저 월간 접속유저 일평균 N-day 잔존율 집계
    select login_year_month
         , '재방문유저' as user_type
         , count(distinct user_id) as mau
         , count(user_id) as mau_not_unique -- mau와 mau_not_unique가 다르다.(재방문유저의 경우, 신규유저와 달리 여러 날짜에 접속할 수 있기 때문)
         -- ⭐️ 재방문 유저의 경우, 접속한 모든 일자에 대해 각각 N-day 잔존율이 계산되기 때문에, 분모를 count(distinct user_id) 방식으로 집계하면 Ret가 과대집계됩니다. 
         , round(sum(case when date_diff_count >= 1 then d1_login end) / count(case when date_diff_count >= 1 then user_id end), 3) as d1_ret
         , round(sum(case when date_diff_count >= 7 then d7_login end) / count(case when date_diff_count >= 7 then user_id end), 3) as d7_ret
         , round(sum(case when date_diff_count >= 14 then d14_login end) / count(case when date_diff_count >= 14 then user_id end), 3) as d14_ret
         , round(sum(case when date_diff_count >= 30 then d30_login end) / count(case when date_diff_count >= 30 then user_id end), 3) as d30_ret
    from d_plus_day_check_login
    group by login_year_month, user_type
    order by login_year_month, user_type
""")

monthlyAvgNdayRetByRVU = query_job.to_dataframe()


##------------------------------------------------------------------------------------------------------------------------------------------------------------##


## << dailyNdayRetByNVU: 유저 타입별 일간 D+day 잔존율 >>
query_job = client.query("""

    -- 월별/일별 신규가입 유저 목록 테이블 (상동)
    with monthly_new_user_list as (
        select create_year_month
             , create_date
             , user_id
        FROM `my_temp.my_infos`
    ), 

    -- 일간 유저별 접속 로그 테이블 (상동)
    daily_login as (
        select distinct login_date
             , login_year_month
             , user_id
        from `my_temp.daily_login_users`
    ),

    -- [재방문유저] 일간 접속유저 D+1/7/14/30 N-day 접속여부 확인 테이블 (상동)
    d_plus_day_check_login as (
        select distinct a.login_date, a.login_year_month
             , date_diff(CAST('2022-11-30' AS DATE), a.login_date, DAY) as date_diff_count -- 추적 기간이 다 차지 않은 경우 예외처리 해주기 위한 컬럼
             , a.user_id
             , case when d1.user_id is not null then 1 end as d1_login
             , case when d7.user_id is not null then 1 end as d7_login
             , case when d14.user_id is not null then 1 end as d14_login
             , case when d30.user_id is not null then 1 end as d30_login
        from (
          select distinct a.login_date, a.login_year_month, a.user_id
          from daily_login as a
          where not exists ( 
            -- 재방문유저만 추려내는 작업
            select 1
            from monthly_new_user_list as b
            where a.user_id = b.user_id and a.login_year_month = b.create_year_month
          )
        ) as a 
        left join (
          select login_date, user_id 
          from daily_login
        ) as d1
        on a.user_id = d1.user_id and date_add(a.login_date, interval 1 day) = d1.login_date
        left join (
          select login_date, user_id 
          from daily_login
        ) as d7
        on a.user_id = d7.user_id and date_add(a.login_date, interval 7 day) = d7.login_date
        left join (
          select login_date, user_id 
          from daily_login
        ) as d14
        on a.user_id = d14.user_id and date_add(a.login_date, interval 14 day) = d14.login_date
        left join (
          select login_date, user_id 
          from daily_login
        ) as d30
        on a.user_id = d30.user_id and date_add(a.login_date, interval 30 day) = d30.login_date
        order by a.login_date, a.user_id
    )

    -- 재방문유저 일간 접속유저 N-day 잔존율 집계
    select login_date
         , '재방문유저' as user_type
         , count(distinct user_id) as dau
         , count(user_id) as dau_not_unique
         , round(sum(d1_login)/count(user_id), 3) as d1_ret
         , round(sum(d7_login)/count(user_id), 3) as d7_ret
         , round(sum(d14_login)/count(user_id), 3) as d14_ret
         , round(sum(d30_login)/count(user_id), 3) as d30_ret
    from d_plus_day_check_login
    group by login_date, user_type
    order by login_date, user_type
""")

dailyNdayRetByNVU = query_job.to_dataframe()

In [ ]:
#@title Visualization-1 ⛳️

## << 재방문유저 월간 일평균 N-day 잔존율 >>

import plotly.express as px
from plotly.subplots import make_subplots

# step.1 - 서브플랏 할당
subfig = make_subplots(specs=[[{"secondary_y": True}]])

# step.2 - fig1(잔존율 그래프) 생성
fig1 = px.line(monthlyAvgNdayRetByRVU, 
              x="login_year_month", 
              y=['d1_ret', 'd7_ret', 'd14_ret', 'd30_ret'],
              line_group="variable", 
              text="value",
              markers=True,
             )
fig1.update_traces(
    yaxis="y2",
    textposition='top center',
    texttemplate='%{text: .1%}',
    hovertemplate = '%{y:.1%}',
)

# step.3 - fig2(mau 그래프) 생성
fig2 = px.bar(monthlyAvgNdayRetByRVU, 
             x="login_year_month", 
             y="mau", 
            )
fig2.update_traces(marker_color='lightgray')  # e.g. red, hotpink, blue, skyblue, ...

# step.4 - subfig에 fig1, fig2를 통합 할당
subfig.add_traces(fig1.data + fig2.data)
subfig.update_layout(
    {
        "title": {
            "text": "<b>< 재방문 유저 월간 일평균 N-day 잔존율 ><b>",
            "x": 0.5,
            "y": 0.9,
            "font": {
                "size": 13
            }
        },
        "xaxis": {
            "title": "",
            "tick0": "2022-05-01",
            "dtick": 'M1',
            "tickformat": "%m월"
        },
        "yaxis": { "title": "MAU(명)", "tickformat": ',' },
        "yaxis2": { "title": "Avg. N-day Retention(%)", "tickformat": '.0%', "range": [0, 0.8]},
        "legend_title_text": "N-day 잔존율",
        "template":'plotly_white',
    }
)

subfig.update_layout(hovermode="x")

# step.5 - secondary_y 축의 gird 만 보이게 하기
subfig['layout']['yaxis1']['showgrid'] = False

# step.6 - 그래프 출력
subfig.show()

> **Note**

- 11월 D+7 ~ D+14 일평균 잔존율의 경우 전체 모수에 대한 집계값이 아니므로 참고용으로만 사용


> **Comment**

- 재방문 유저의 월간 일평균 잔존율 계산시 당월 신규가입자가 제외되었음에도 11월 일평균 D+1 잔존율은 64.5%로 전월比 3.8%p 상승
- 앞서 < 가입 연월별 MAU > 장표 분석에서 22년 11월 이전 모객 유저그룹의 11월 MAU 볼륨이 증가 또는 소폭 감소한 것과 같은 결과로 해석할 수 있으며
- **다판다마켓에서 공급하는 신규 상품으로 인해 기존 사용자의 잔존율이 올라간게 아닌지 확인 필요**

In [ ]:
#@title Visualization-2

## << 재방문 유저 N-day 잔존율 >>

import plotly.express as px
from plotly.subplots import make_subplots

# step.1 - 서브플랏 할당
subfig = make_subplots(specs=[[{"secondary_y": True}]])

# step.3 - fig1(잔존율 그래프) 생성
fig1 = px.line(dailyNdayRetByNVU, 
              x="login_date", 
              y=['d1_ret', 'd7_ret', 'd14_ret', 'd30_ret'],
              color="variable", 
              # markers=True,
             )
fig1.update_traces(yaxis="y2") # fig1의 y축을 보조축으로 변환

# step.4 - fig2(dau 그래프) 생성
fig2 = px.bar(dailyNdayRetByNVU, 
             x="login_date", 
             y="dau", 
            )
fig2.update_traces(marker_color='lightgray')

# step.5 - subfig에 fig1, fig2를 통합 할당
subfig.add_traces(fig1.data + fig2.data)
subfig.update_layout(
    {
        "title": {
            "text": "<b>< 재방문 유저 N-day 잔존율 ><b>",
            "x": 0.5,
            "y": 0.8,
            "font": {
                "size": 13
            }
        },
        "xaxis1": {
            "title": "",
            "tick0": "2022-05-01",
            "dtick": 'M1',
            "tickformat": "%Y-%m-%d"
        },
        "yaxis": { "title": "DAU(명)", "tickformat": ',', "range": [0, 2500]},
        "yaxis2": { "title": "N-day Retention(%)", "tickformat": '.1%', "range": [0, 1]},
        "legend_title_text": "N-day 잔존율",
        "template":'plotly_white',
    }
)

# step.6 - 잔존율 탐색 기준선 도식
subfig.add_hline(y=0.7, 
                 line_dash="dot", 
                 secondary_y=True,
                 )
# step.6 - 잔존율 탐색 기준선 관련 내용 표기
subfig.add_annotation(
    x='2022-11-07',
    y=1750,
    xref="x",
    yref="y",
    text="잔존율 70% 기준선",
    showarrow=True,
    font=dict(
        size=12,
        color="Gray"
    ),
    align="right",
    arrowhead=2,
    ax=-20,
    ay=-60
)


# step.7 - 신규 매장 입점 기간 표시
subfig.add_vrect(x0="2022-06-13", 
                 x1="2022-06-16",
                 annotation_text="* 신규 매장 입점(6/14 ~ 6/15)", 
                 annotation_position="top left",
                 fillcolor="skyblue", opacity=0.25, line_width=0)

subfig.add_vrect(x0="2022-11-06", 
                 x1="2022-11-09",
                 annotation_text="* 신규 매장 입점(11/7 ~ 11/8)", 
                 annotation_position="top right",
                 fillcolor="skyblue", opacity=0.25, line_width=0)

subfig.add_vrect(x0="2022-11-21", 
                 x1="2022-11-30",
                 annotation_text="* 11월 3주차 ~", 
                 annotation_position="top right",
                 fillcolor="hotpink", opacity=0.25, line_width=0)


subfig.add_hrect(
                  y0=1500,
                  y1=1900,
                 fillcolor="yellow", opacity=0.25, line_width=0)


# step.8 - secondary_y 축의 gird 만 보이게 하기
subfig['layout']['yaxis1']['showgrid'] = False

# step.9 - 그래프 출력
subfig.show()


> **Comment**

- 재방문 유저의 11월 D+1 잔존율과 DAU 모두 10월보다 소폭 상단에 배치된 것을 확인할 수 있음

## < 지역별 잔존율 현황 >

In [ ]:
#@title Make DataFrame

## << weeklyRetByRegion: 지역별 주간 일평균 D+day 잔존율 >>
query_job = client.query("""

    -- 월별/일별 신규가입 유저 목록 테이블 (상동)
    with new_user_list as (
        select distinct create_year_month
             , create_date
             , region_3depth_name	 as region
             , user_id
        FROM `my_temp.my_infos`
    ), 


    -- 일간(주차 정보 포함) 접속 로그 테이블
    daily_login as (
        select distinct login_date
             , login_year_month
             , extract(DAYOFWEEK from date_add(login_date, interval -1 day)) as dayofweek_num -- DAYOFWEEK: 한 주의 첫날이 일요일인 [1,7] 범위의 값을 반환합니다. (실제 날짜에 -1일을 차감해서 월요일부터 1로 시작하도록 변경 ⭐️)
             , extract(WEEK from date_add(login_date, interval -1 day)) as week_num -- WEEK: [0, 53] 범위에서 날짜의 주 번호를 반환합니다. 주는 일요일부터 시작되며 그 해의 첫 번째 일요일 이전 날짜는 0번째 주에 속합니다.
             , user_id
        from `my_temp.daily_login_users`
        order by login_date
    ),

    -- [전체유저] 일간 접속유저 D+1/7/14/30 N-day 접속여부 확인 테이블
    d_plus_day_check_login as (
        select distinct a.login_date, a.login_year_month
             , date_diff(CAST('2022-11-30' AS DATE), a.login_date, DAY)  as date_diff_count
             , a.user_id, a.week_num
             , case when d1.user_id is not null then 1 end as d1_login
             , case when d7.user_id is not null then 1 end as d7_login
             , case when d14.user_id is not null then 1 end as d14_login
             , case when d30.user_id is not null then 1 end as d30_login
        from (
          select distinct login_date, login_year_month, user_id, week_num
          from daily_login
        ) as a 
        left join (
          select login_date, user_id 
          from daily_login
        ) as d1
        on a.user_id = d1.user_id and date_add(a.login_date, interval 1 day) = d1.login_date
        left join (
          select login_date, user_id 
          from daily_login
        ) as d7
        on a.user_id = d7.user_id and date_add(a.login_date, interval 7 day) = d7.login_date
        left join (
          select login_date, user_id 
          from daily_login
        ) as d14
        on a.user_id = d14.user_id and date_add(a.login_date, interval 14 day) = d14.login_date
        left join (
          select login_date, user_id 
          from daily_login
        ) as d30
        on a.user_id = d30.user_id and date_add(a.login_date, interval 30 day) = d30.login_date
        order by a.login_date, a.user_id
    )

    -- 전체유저 주간 접속유저 일평균 N-day 잔존율 집계
    select week_num, region
         , min(login_date) as login_date -- 매주 월요일 날짜
         , count(distinct login_date) as day_cnt -- 추적 기간 7일을 모두 채운 주차에 대해서만 집계하기 위한 필터링 컬럼
         , count(distinct user_id) as wau
         , count(user_id) as wau_not_unique
         , round(safe_divide(sum(case when date_diff_count >= 1 then d1_login end), count(case when date_diff_count >= 1 then user_id end)), 3) as d1_ret
         , round(safe_divide(sum(case when date_diff_count >= 7 then d7_login end), count(case when date_diff_count >= 7 then user_id end)), 3) as d7_ret
         , round(safe_divide(sum(case when date_diff_count >= 14 then d14_login end), count(case when date_diff_count >= 14 then user_id end)), 3) as d14_ret
         , round(safe_divide(sum(case when date_diff_count >= 30 then d30_login end), count(case when date_diff_count >= 30 then user_id end)), 3) as d30_ret
    from (
      -- 접속 정보 테이블에 거주지역 정보(region 컬럼) 붙이는 작업
      select a.login_date, a.login_year_month, a.date_diff_count
             , a.user_id
             , d1_login
             , d7_login
             , d14_login
             , d30_login
             , b.region
             , week_num
      from d_plus_day_check_login as a
      inner join new_user_list as b
      on a.user_id = b.user_id
    ) as a
    group by a.week_num, a.region
    having day_cnt = 7 -- 7일이 모두찬 주차의 데이터만 사용
    order by week_num, region
""")

weeklyRetByRegion = query_job.to_dataframe()

In [ ]:
#@title Visualization-1


import plotly.express as px

# step.1 - 테이블을 시각화 하기 위한 형태로 변환
wauByRegionMelt = pd.melt(weeklyRetByRegion, id_vars=['login_date', 'week_num', 'region'], value_vars=['wau'])

# step.2 - fig1(WAU 그래프) 생성
fig = px.bar(wauByRegionMelt, 
              x="login_date", 
              y="value", 
              color="region", 
              text="value",
             )

## step.3 - text 표현 형식과, 출력 위치를 조정
fig.update_traces(texttemplate='%{text:,}명',
                  textposition='inside') 

## step.4 - fig의 layout 설정 변경
fig.update_layout(
    {
        "title": {
            "text": "<b>< 지역별 WAU ><b>",
            "x": 0.5,
            "y": 0.95,
            "font": {
                "size": 13
            }
        },
        "yaxis": { "title": "WAU(명)", "tickformat": ','  }, 
        "xaxis": {
            "title": "",
            "tick0": "2022-05-01",
            "dtick": 'M1',
            "tickformat": "%Y-%m-%d"
        },
        "legend_title_text": "사용자 거주지역",
        "template":'plotly_white',
        "height":400,
    },

)

# step.5 - 신규 매장 입점 기간 표시
fig.add_vrect(x0="2022-06-10", 
              x1="2022-06-16",
              annotation_text="* 신규 매장 입점 주간(오픈일: 6/14 ~ 6/15)", 
              annotation_position="top left",
              fillcolor="skyblue", opacity=0.25, line_width=0)

fig.add_vrect(x0="2022-11-04", 
              x1="2022-11-10",
              annotation_text="* 신규 매장 입점 주간(오픈일: 11/7 ~ 11/8)", 
              annotation_position="top right",
              fillcolor="skyblue", opacity=0.25, line_width=0)

# step.6 - 그래프 출력
fig.show()

In [ ]:
#@title Visualization-2

import plotly.express as px

# step.1 - 테이블을 시각화 하기 위한 형태로 변환
wauNdayRetByRegionMelt = pd.melt(weeklyRetByRegion, id_vars=['login_date', 'week_num', 'region'], value_vars=['d1_ret', 'd7_ret', 'd14_ret', 'd30_ret'])

# step.2 - fig1(지역별 잔존율 그래프) 생성
fig = px.line(wauNdayRetByRegionMelt, 
              x="login_date", 
              y="value", 
              color="region", 
              facet_row="variable",
              markers=True,
             )

## step.3 - fig의 layout 설정 변경
fig.update_layout(
    {
        "title": {
            "text": "<b>< 지역별 주간 일평균 N-day 잔존율 ><b>",
            "x": 0.5,
            "y": 0.95,
            "font": {
                "size": 13
            }
        },
        "yaxis": { "tickformat": '.0%'}, # "tickformat": '.0%' 
        "yaxis2": { "tickformat": '.0%'},
        "yaxis3": { "tickformat": '.0%'},
        "yaxis4": { "tickformat": '.0%'},
        "xaxis": {
            "title": "",
            "tick0": "2022-06",
            "dtick": 'M1',
            "tickformat": "%Y-%m-%d" #"%m월" # "%y-%m"
        },

        "legend_title_text": "사용자 설정 지역",
        # "template":'plotly_white',
        "height": 600,
    },
)

# step.4 - 그래프 마우스 오버시 hovermode x축으로 설정
fig.update_layout(hovermode="x")

# step.5 - 신규 매장 입점 기간 표시
fig.add_vrect(x0="2022-06-10", 
              x1="2022-06-16",
              annotation_text="* 신규 매장 오픈 주간(오픈일: 6/14 ~ 6/15)", 
              annotation_position="top left",
              fillcolor="skyblue", opacity=0.25, line_width=0)

fig.add_vrect(x0="2022-11-04", 
              x1="2022-11-10",
              annotation_text="* 신규 매장 오픈 주간(오픈일: 11/7 ~ 11/8)", 
              annotation_position="right top",
              fillcolor="skyblue", opacity=0.25, line_width=0)

# step.6 - 그래프 출력 
fig.show()

> **Comment**

- 기존 매장 지역(목동)과 다판다마켓 실수요 지역(독산3동, 당산동4가, 당산동5가, 양평동3가, 양평동4가, 여의도동) 비교시
- **기존 로컬팜의 핵심 매장이었던 목동보다 다판다마켓 실 수요지역의 잔존율이 더 높게 집계되는 것을 확인**  
- 이러한 추세가 유지될 경우, **로컬팜과 다판다마켓의 판매 품목 및 팡매방식 비교 분석을 통해 기존 로컬팜 서비스 지역의 매출을 견할 수 있는 전략 도출 필요**


# **[ 매출 현황 분석 ]**

## < 요약 ✨ >

> **매출 상승요인**
  - 다판다마켓 인수의 영향으로 11월 매출 1.4억원 달성(전월比 160% 상승) 
  - PU, ARPPU, PURCHASE_CNT 모두 전월比 30 ~ 152% 증가하여 매출 상승에 복합적으로 영향을 미침

> **신규상품 공급 효과**
  - 다판다마켓 셀러였던 김정식님이 새로운 상품을 공급함에 따라 기존 로컬팜 매장의 11월 매출이 전월比 24 ~ 52% 상승
  - 기존 로컬팜 매장에서 발생한 김정식님 상품에 대한 매출은 과반 이상이 기존 유저들로 인해 발생
  - 재구매 그룹(retained, resurrected)의 11월 매출 또한 25%가 김정식님 상품으로부터 발생한 것으로 보아 신규상품을 공급하는 것이 기존 유저들의 재구매를 유발하 것으로 추정됨
  - 바꿔 말하면, 기존 유저들의 구매전환을 지속시키기 위해서는 꾸준한 신규상품 공급이 필요

## < 월간 매출지표 현황 >

In [ ]:
#@title Make DataFrame ⛳️

## << monthlySalesIndexDf: 월간 매출 기본지표 >>
query_job = client.query("""
  with mau as (
    select login_year_month, count(distinct user_id) as mau
    from `my_temp.daily_login_users`
    where login_year_month between '2022-05' and '2022-11'
    group by login_year_month
  ),

  sales_index as (
    select order_year_month, count(distinct user_id) as PU, sum(payment_amount) as SALES, round(sum(payment_amount)/count(distinct user_id)) as ARPPU, count(distinct order_id) as PURCHASE_CNT
    from `my_temp.orders`
    where payment_status = 'completed'
      and order_year_month between '2022-05' and '2022-11'
    group by order_year_month
  ),

  product_regist_count as (
    select format_date("%Y-%m", registration_date) as registration_year_month, count(distinct product_id) as REGISTRATION_CNT
    from `localparm_dw.products`
    where format_date("%Y-%m", registration_date) between '2022-05' and '2022-11'
    group by registration_year_month
  )

  select a.login_year_month as year_month, MAU, PU, round(pu/mau, 3) as PUR, SALES, ARPPU, PURCHASE_CNT, REGISTRATION_CNT
  from mau as a
  left join sales_index as b
  on a.login_year_month = b.order_year_month
  left join product_regist_count as c
  on a.login_year_month = c.registration_year_month
  order by login_year_month
""")
monthlySalesIndexDf = query_job.to_dataframe()



## << monthlySalesIndexOfExistingShopDf: 기존 로컬팜 매장의 월간 매출 기본지표 >>
query_job = client.query("""
  with sales_index as (
    select order_year_month, count(distinct user_id) as PU, sum(payment_amount) as SALES, round(sum(payment_amount)/count(distinct user_id)) as ARPPU, count(distinct order_id) as PURCHASE_CNT
    from `my_temp.orders`
    where payment_status = 'completed'
      and order_year_month between '2022-05' and '2022-11'
      and pickup_shop_name not in ('픽업존(GS영등포당산점)', '픽업존(다이소 난곡사거리점)', '픽업존(더현대서울)') -- 11월에 오픈한 매장 제외
    group by order_year_month
  )

  select order_year_month as year_month, PU, SALES, ARPPU, PURCHASE_CNT
  from sales_index 
  order by year_month
""")
monthlySalesIndexOfExistingShopDf = query_job.to_dataframe()



## << weeklySalesIndexDf: 주간 매출 기본지표 >>
query_job = client.query("""
  with mau as (
    select extract(WEEK from date_add(login_date, interval -1 day)) as week_num -- WEEK: [0, 53] 범위에서 날짜의 주 번호를 반환합니다. 주는 일요일부터 시작되며 그 해의 첫 번째 일요일 이전 날짜는 0번째 주에 속합니다.
         , count(distinct user_id) as mau
    from `my_temp.daily_login_users`
    where login_year_month between '2022-05' and '2022-10' -- 편향을 제외하기 위해 11월 제외
    group by week_num
  ),

  sales_index as (
    select extract(WEEK from date_add(order_date, interval -1 day)) as week_num -- WEEK: [0, 53] 범위에서 날짜의 주 번호를 반환합니다. 주는 일요일부터 시작되며 그 해의 첫 번째 일요일 이전 날짜는 0번째 주에 속합니다.
         , count(distinct user_id) as PU, sum(payment_amount) as SALES, round(sum(payment_amount)/count(distinct user_id)) as ARPPU, count(distinct order_id) as PURCHASE_CNT
    from `my_temp.orders`
    where payment_status = 'completed'
      and order_year_month between '2022-05' and '2022-10' -- 편향을 제외하기 위해 11월 제외
    group by week_num
  ),

  product_regist_count as (
    select extract(WEEK from date_add(registration_date, interval -1 day)) as week_num -- WEEK: [0, 53] 범위에서 날짜의 주 번호를 반환합니다. 주는 일요일부터 시작되며 그 해의 첫 번째 일요일 이전 날짜는 0번째 주에 속합니다.
         , count(distinct product_id) as REGISTRATION_CNT
    from `localparm_dw.products`
    where format_date("%Y-%m", registration_date) between '2022-05' and '2022-10' -- 편향을 제외하기 위해 11월 제외
    group by week_num
  )

  select a.week_num, MAU, PU, round(pu/mau, 3) as PUR, SALES, ARPPU, PURCHASE_CNT, REGISTRATION_CNT
  from mau as a
  left join sales_index as b
  on a.week_num = b.week_num
  left join product_regist_count as c
  on a.week_num = c.week_num
  order by week_num
""")
weeklySalesIndexDf = query_job.to_dataframe()

In [ ]:
#@title Visualization-1 ⛳️
# --- << 장표: 월간 지역별 신규 유저수  >> --------------------------------------------------------------------------------------#

import plotly.graph_objects as go
from plotly.subplots import make_subplots

# step.1 - 여러개의 그래프를 그리기 위한 (6 x 1)형태의 subplots 설정
fig = make_subplots(
    rows=6, cols=1, 
    vertical_spacing=0.04,
    specs=[[{"secondary_y": True}], [{"secondary_y": True}], [{"secondary_y": True}], [{"secondary_y": True}], [{"secondary_y": True}], [{"secondary_y": True}]], 
    # https://stackoverflow.com/questions/70434181/plotly-subplots-issue-with-specs-value-error # 🔥
    # https://community.plotly.com/t/dash-the-specs-argument-to-make-subplots-must-be-a-2d-list-of-dictionaries-with-dimensions-2-x-2/40034
)

# step.2 - fig(subplot)에 add_trace()를 사용해 각 행별로 MAU, PUR, SALES, PU, ARPPU, PURCHASE_CNT, REGISTRATION_CNT 그래프를 순차적으로 할당 
fig.add_trace(
    go.Bar(    
        x=monthlySalesIndexDf['year_month'], 
        y=monthlySalesIndexDf['MAU'],
        name='MAU',
        marker_color="skyblue", # MAU 11월 색 강조        
    ),
    secondary_y=False,
    row=1, col=1,
)

fig.add_trace(
    go.Scatter(
        x=monthlySalesIndexDf['year_month'], 
        y=monthlySalesIndexDf['PUR'], 
        name='PUR', 
        mode='lines+markers+text', 
        text=monthlySalesIndexDf['PUR'], 
        textposition='top center',
        texttemplate='%{text:.1%}',
        hovertemplate="%{y:.1%}",
    ),
    secondary_y=True,
    row=1, col=1,
)

fig.add_trace(
    go.Scatter(
        x=monthlySalesIndexDf['year_month'], 
        y=monthlySalesIndexDf['SALES'], 
        mode='lines+markers+text', 
        name='SALES', 
        text=monthlySalesIndexDf['SALES'],
        textposition='top center',
        texttemplate='%{text:,}원',
        hovertemplate="%{y:,}원",
    ),
    row=2, col=1
)

fig.add_trace(
    go.Scatter(
        x=monthlySalesIndexDf['year_month'], 
        y=monthlySalesIndexDf['PU'], 
        mode='lines+markers+text', 
        name='PU',
        text=monthlySalesIndexDf['PU'],
        textposition='top center',
        texttemplate='%{text:,}명',
        hovertemplate="%{y:,}명",
    ),
    row=3, col=1
)

fig.add_trace(
    go.Scatter(
        x=monthlySalesIndexDf['year_month'], 
        y=monthlySalesIndexDf['ARPPU'], 
        mode='lines+markers+text', 
        name='ARPPU',
        text=monthlySalesIndexDf['ARPPU'],
        textposition='top center',
        texttemplate='%{text:,}원',
        hovertemplate="%{y:,}원",
    ),
    row=4, col=1
)


fig.add_trace(
    go.Scatter(
        x=monthlySalesIndexDf['year_month'], 
        y=monthlySalesIndexDf['PURCHASE_CNT'], 
        mode='lines+markers+text', 
        name='PURCHASE_CNT',
        text=monthlySalesIndexDf['PURCHASE_CNT'],
        textposition='top center',
        texttemplate='%{text:,}개',
        hovertemplate="%{y:,}개",
    ),
    row=5, col=1
)

fig.add_trace(
    go.Scatter(
        x=monthlySalesIndexDf['year_month'], 
        y=monthlySalesIndexDf['REGISTRATION_CNT'], 
        mode='lines+markers+text', 
        name='REGISTRATION_CNT',
        text=monthlySalesIndexDf['REGISTRATION_CNT'],
        textposition='top center',
        texttemplate="%{text:,}개",
        hovertemplate="%{y:,}개",
    ),
    row=6, col=1
)



# step.3 - 그래프 레이아웃 업데이트
# 각 그래프별로 y축에 대한 range, title, tickformat 등을 설정하고자 할 경우 어떤 y축에 대한 설정인지를 숫자로 구분해 주고 있습니다. 
# ㄴ 앞서 step.1에서 subplot 선언시 이중축에 대해 허용했기 때문에 y축에 대한 레이아웃 설정이 왼쪽축/오른쪽축 모두 가능합니다.
fig.update_layout(
    
    {
        "title": {
            "text": "<b>< 매출지표 월간 추이 ><b>",
            "x": 0.5,
            "y": 0.95,
            "font": {
                "size": 13
            }
        },
        "yaxis1": {
            "range":[0, 8000],
            "tickformat": ',',
            "title": "MAU(명)",
            "showgrid": False,
        },
        "yaxis2": { 
            "title": "PUR",
            "tickformat": '.0%',
            "range": [0.25, 0.6],
        },

        "yaxis3": {
            "range":[0, 200000000],
            "title": "SALES(원)"
        },
        "yaxis5": {
            "range":[0, 3000],
            "title": "PU(명)",
            "tickformat": ","
        },
        "yaxis7": {
            "range":[20000, 80000],
            "title": "ARPPU(원)"
        },
        "yaxis9": {
            "range":[0, 15000],
            "title": "구매횟수(개)"
        },
        "yaxis11": {
            "range":[0, 400],
            "title": "상품등록수(개)"
        },     
        "template":'plotly',
        "legend_traceorder": "normal", #normal(default - 데이터 순서대로), reversed
        "height": 900 
    },    
)

# step.4 - 그래프 마우스 오버시 hovermode x축으로 설정
fig.update_layout(hovermode="x")

# step.5 - 모든 x축에 대한 일괄 설정
fig['layout']['yaxis1']['showgrid'] = False
fig.update_xaxes(showgrid=False)
fig.update_xaxes(title = "", tick0 = "2022-05", dtick="M1", tickformat="%Y-%m")


# step.6 - 10월 11월 구간 표시
fig.add_vrect(x0="2022-09-15", 
              x1="2022-11-15",
              annotation_text="", 
              annotation_position="top left",
              fillcolor="hotpink", opacity=0.25, line_width=0)

# step.7 - 그래프 출력
fig.show()

> **Comment**

- 11월 모든 매출 지표 전월比 상승 
  - 증감률: **PUR** +28.5%, **SALES** +160.5%, **PU** +99.5%, **ARPPU** +30.7%, **PURCHASE_CNT**: +152.9%, **REGISTRATION_CNT**: +174.7%

In [ ]:
#@title Visualization-2
# --- << 장표: 월간 지역별 신규 유저수  >> --------------------------------------------------------------------------------------#

import plotly.graph_objects as go
from plotly.subplots import make_subplots

# step.1 - 여러개의 그래프를 그리기 위한 (6 x 1)형태의 subplots 설정
fig = make_subplots(
    rows=4, cols=1, 
    vertical_spacing=0.04,
    )

# step.2 - fig(subplot)에 add_trace()를 사용해 각 행별로 MAU, PUR, SALES, PU, ARPPU, PURCHASE_CNT, REGISTRATION_CNT 그래프를 순차적으로 할당 
fig.add_trace(
    go.Scatter(
        x=monthlySalesIndexOfExistingShopDf['year_month'], 
        y=monthlySalesIndexOfExistingShopDf['SALES'], 
        mode='lines+markers+text', 
        name='SALES', 
        text=monthlySalesIndexOfExistingShopDf['SALES'],
        textposition='top center',
        texttemplate='%{text:,}원',
        hovertemplate="%{y:,}원",
    ),
    row=1, col=1
)

fig.add_trace(
    go.Scatter(
        x=monthlySalesIndexOfExistingShopDf['year_month'], 
        y=monthlySalesIndexOfExistingShopDf['PU'], 
        mode='lines+markers+text', 
        name='PU',
        text=monthlySalesIndexOfExistingShopDf['PU'],
        textposition='top center',
        texttemplate='%{text:,}명',
        hovertemplate="%{y:,}명",
    ),
    row=2, col=1
)

fig.add_trace(
    go.Scatter(
        x=monthlySalesIndexOfExistingShopDf['year_month'], 
        y=monthlySalesIndexOfExistingShopDf['ARPPU'], 
        mode='lines+markers+text', 
        name='ARPPU',
        text=monthlySalesIndexOfExistingShopDf['ARPPU'],
        textposition='top center',
        texttemplate='%{text:,}원',
        hovertemplate="%{y:,}원",
    ),
    row=3, col=1
)


fig.add_trace(
    go.Scatter(
        x=monthlySalesIndexOfExistingShopDf['year_month'], 
        y=monthlySalesIndexOfExistingShopDf['PURCHASE_CNT'], 
        mode='lines+markers+text', 
        name='PURCHASE_CNT',
        text=monthlySalesIndexOfExistingShopDf['PURCHASE_CNT'],
        textposition='top center',
        texttemplate='%{text:,}개',
        hovertemplate="%{y:,}개",
    ),
    row=4, col=1
)


# step.3 - 그래프 레이아웃 업데이트
# 각 그래프별로 y축에 대한 range, title, tickformat 등을 설정하고자 할 경우 어떤 y축에 대한 설정인지를 숫자로 구분해 주고 있습니다. 
# ㄴ 앞서 step.1에서 subplot 선언시 이중축에 대해 허용했기 때문에 y축에 대한 레이아웃 설정이 왼쪽축/오른쪽축 모두 가능합니다.
fig.update_layout(
    
    {
        "title": {
            "text": "<b>< 기존 로컬팜 매장 - 매출지표 월간 추이 ><b>",
            "x": 0.5,
            "y": 0.95,
            "font": {
                "size": 13
            }
        },
        "yaxis1": {
            "range":[0, 200000000],
            "title": "SALES(원)"
        },
        "yaxis2": {
            "range":[0, 3000],
            "title": "PU(명)",
            "tickformat": ","
        },
        "yaxis3": {
            "range":[20000, 80000],
            "title": "ARPPU(원)"
        },
        "yaxis4": {
            "range":[0, 15000],
            "title": "구매횟수(개)"
        },
        "template":'plotly',
        "legend_traceorder": "normal", #normal(default - 데이터 순서대로), reversed
        "height": 600 
    },    
)

# step.4 - 그래프 마우스 오버시 hovermode x축으로 설정
fig.update_layout(hovermode="x")

# step.5 - 모든 x축에 대한 일괄 설정
fig['layout']['yaxis1']['showgrid'] = False
fig.update_xaxes(showgrid=False)
fig.update_xaxes(title = "", tick0 = "2022-05", dtick="M1", tickformat="%Y-%m")


# step.6 - 10월 11월 구간 표시
fig.add_vrect(x0="2022-09-15", 
              x1="2022-11-15",
              annotation_text="", 
              annotation_position="top left",
              fillcolor="hotpink", opacity=0.25, line_width=0)

# step.7 - 그래프 출력
fig.show()

> **Comment**

- 신규 오픈 매장을 제외한 기존 5개 매장의 11월 매출 지표 또한 전월比 상승  
  - 증감률: **SALES** +77.4%, **PU** +41.3%, **ARPPU** +25.6%, **PURCHASE_CNT**: +85.9%
- 11월 다판다마켓 입점 이후 기존 로컬팜 매장의 매출까지 동반 성장한 것으로 보아 어떤 요인이 매출 상승에 영향을 미쳤는지 확인 필요 

## < 판매자별 매출 기여도 >

In [ ]:
#@title Make DataFrame-1

## << novSalesInfoByUserDf: 월별 판매자별 매출 >>
query_job = client.query("""
  select b.user_id, c.nickname, a.order_year_month, sum(a.payment_amount) as sales
  from `my_temp.orders` as a
  left join `localparm_dw.products` as b
  on a.product_id = b.product_id
  left join `my_temp.my_infos` as c
  on b.user_id = c.user_id
  where a.payment_status = 'completed'
  group by b.user_id, c.nickname, a.order_year_month
  order by a.order_year_month, b.user_id, c.nickname
""")
monthlySalesBySellerDf = query_job.to_dataframe()



## << monthlySalesByShopAndSellerDf: 월별 매장별 판매자별 매출 >>
query_job = client.query("""
  select a.order_year_month, a.pickup_shop_name, c.nickname, sum(a.payment_amount) as sales
  from `my_temp.orders` as a
  left join `localparm_dw.products` as b
  on a.product_id = b.product_id
  left join `my_temp.my_infos` as c
  on b.user_id = c.user_id
  where a.payment_status = 'completed'
  group by a.order_year_month, a.pickup_shop_name, c.nickname
  order by a.order_year_month, a.pickup_shop_name, c.nickname
""")
monthlySalesByShopAndSellerDf = query_job.to_dataframe()


## << novSalesByShopAndUserTypeDf: 11월 김정식 셀러 판매상품에 대한 기존 매장별 유저타입(신규/기존)별 매출 >>
query_job = client.query("""

  with sales_by_user_type as (
    select a.order_year_month
        , a.pickup_shop_name
        , case when d.user_id is null then '재방문유저'
                else '신규유저'
          end user_type
        , sum(a.payment_amount) as sales
        , count(distinct a.user_id) as pu
    from `my_temp.orders` as a
    -- 상품 정보를 붙인다.(판매자 정보를 붙이기 위한 사전 작업)
    left join `localparm_dw.products` as b
    on a.product_id = b.product_id
    -- 판매자 정보를 붙인다.
    left join `my_temp.my_infos` as c 
    on b.user_id = c.user_id
    -- 구매자의 유저타입(신규/재방문 유저) 정보를 붙인다
    left join `my_temp.my_infos` as d
    on a.user_id = d.user_id and a.order_year_month = d.create_year_month
    where a.payment_status = 'completed'
      and a.pickup_shop_name not in ('픽업존(GS영등포당산점)', '픽업존(다이소 난곡사거리점)', '픽업존(더현대서울)') -- 11월에 오픈한 매장 제외 (기존 로컬팜 매장만 선택)
      and c.nickname = '김정식-2cca8b6e' -- 다판다마켓 판매자의 상품 구매내역만 선택
      and a.order_year_month = '2022-11'
    group by a.order_year_month
          , a.pickup_shop_name
          , case when d.user_id is null then '재방문유저'
                  else '신규유저'
            end
  ), 

  sales_by_user_type_all as (
    select pickup_shop_name, user_type, sales, pu
    from sales_by_user_type

    union all

    select '픽업존(통합)' as pickup_shop_name, user_type, sum(sales) as sales, sum(pu) as pu
    from sales_by_user_type
    group by user_type
  )

  select pickup_shop_name, user_type, sales, pu
  from sales_by_user_type_all
  order by case when pickup_shop_name = '픽업존(통합)' then 0
                when pickup_shop_name = '픽업존(유승상가)' then 1
                when pickup_shop_name = '픽업존(메이비카페)' then 2 
                when pickup_shop_name = '픽업존(서울드림신용협동조합)' then 3 
                when pickup_shop_name = '픽업존(GS25 목동3동점)' then 4 
                when pickup_shop_name = '픽업존(참맛부대찌개아구찜)' then 5 
                when pickup_shop_name = '픽업존(GS영등포당산점)' then 6 
                when pickup_shop_name = '픽업존(다이소 난곡사거리점)' then 7 
                when pickup_shop_name = '픽업존(더현대서울)' then 8 
            end
          , user_type
""")
novSalesByShopAndUserTypeDf = query_job.to_dataframe()




In [ ]:
#@title Visualization-1

## << 월간 판매자별 SALES >> 

import plotly.express as px

fig = px.bar(monthlySalesBySellerDf, 
              x="order_year_month", 
              y="sales", 
              color="nickname", 
              text="sales",
              # facet_row="region_name",
             )

fig.update_traces(texttemplate='%{text:,}원', textposition='inside',)

fig.update_layout(
    {
        "title": {
            "text": "<b>< 판매자별 월간 SALES ><b>",
            "x": 0.5,
            "y": 0.95,
            "font": {
                "size": 13
            }
        },
        "yaxis": { "title": "SALES(원)", "tickformat": ','  }, 
        "xaxis": {
            "title": "",
            "tick0": "2022-05",
            "dtick": 'M1',
            "tickformat": "%Y-%m"
        },
        "legend_title_text": "판매자 닉네임",
        "template":'plotly_white',
    }
)


fig.show()

> **Comment**

- 판매자별로 월간 매출을 집계해 보면 김지은, 양민석님의 11월 매출은 (10월 or 9월)과 유사한 수준을 유지중 이며
- **신규 판매자 김정식님의 경우 11월 매출은 기존 로컬팜 셀러들의 매출을 상회하는 7.8천만원 달성**

In [ ]:
#@title Visualization-2

## << 월별 매장별 판매자별 매출 >>
import plotly.express as px

## step.1 - fig에 px.bar() 그래프 담기
fig = px.bar(monthlySalesByShopAndSellerDf, 
             x='order_year_month', 
             y='sales',
             text='sales',
             color='nickname',
             barmode="group", 
             facet_col="pickup_shop_name",
             facet_col_wrap=4,
             facet_col_spacing = 0.05,
             facet_row_spacing = 0.2, #  (float between 0 and 1) – Spacing between facet rows, in paper units. Default is 0.03 or 0.0.7 when facet_col_wrap is used.
             category_orders={"pickup_shop_name": ['픽업존(유승상가)', '픽업존(메이비카페)', '픽업존(서울드림신용협동조합)', '픽업존(GS25 목동3동점)', '픽업존(참맛부대찌개아구찜)', '픽업존(GS영등포당산점)', '픽업존(다이소 난곡사거리점)', '픽업존(더현대서울)'],
                              "order_year_month": ["2022-05", "2022-06", "2022-07", "2022-08", "2022-09", "2022-10", "2022-11"]},               
            )

## Step.2 - update_trace를 통한 text 형태 및 표현방식 설정
fig.update_traces(textposition='inside', texttemplate='%{text:,}원',) # 왜 bar에서 안하고 여기서 하는지. https://plotly.com/python/text-and-annotations/

## Step.3 - fig의 layout 설정 변경
fig.update_layout(
    {
        "title": {
            "text": "<b>< 월별 매장별 판매자별 매출 비교 ><b>",
            "x": 0.5,
            "y": 0.99,
            "font": {
                "size": 14
            }
        },
        "template":'plotly_white',
        "legend_traceorder": "reversed",
        "legend_title_text": "판매자 닉네임",
        "height": 600,
    }
)


## Step.4 - fig의 x축, y축 일괄 설정
fig.update_xaxes(showticklabels=True , matches=None,
                 title= "", tick0="2022-05", dtick="M1", tickformat="%Y-%m")
fig.update_yaxes(showticklabels=True)


## Step.5 - 그래프 출력
fig.show()

> **Comment**

- 기존 5개(유승상가/메이비카페/서울드림신용협동조합/GS25목동3동점/참맛부대찌개아구찜) 매장의 11월 매출 중 24 ~ 52%를 다판다마켓 상품들이 차지

In [ ]:
#@title Visualization-3

## << 김정식님(다판다마켓 셀러) 판매상품에 대한 기존 유저들의 구매 현황 >>

## step.1 - 시각화 하기 위한 형태로 데이터 핸들링
novSalesByShopAndUserTypeMeltDf = novSalesByShopAndUserTypeDf.melt(id_vars=['pickup_shop_name', 'user_type'], value_vars=['sales', 'pu'])


import plotly.express as px

## step.2 - fig에 px.line() 그래프 담기
fig = px.line(novSalesByShopAndUserTypeMeltDf, 
              x="pickup_shop_name", 
              y= "value", 
              color="user_type",
              facet_col = "variable",
              facet_col_spacing = 0.06, #  (float between 0 and 1) – Spacing between facet rows, in paper units. Default is 0.03 or 0.07 when facet_col_wrap is used.
              markers=True,
              )

## Step.3 - fig의 layout 설정 변경
fig.update_layout(
    {
        "title": {
            "text": "<b>< 11월 기준 - 다판다마켓 공급 상품에 대한 기존 매장의 판매 현황 ><b>",
            "x": 0.5,
            "y": 0.99,
            "font": {
                "size": 15
            }
        },
        "yaxis1": {
            "title": "SALES(원)",
            "tickformat": ","
        },
        "yaxis2": {
            "title": "PU(명)",
            "tickformat": ","
        },
        "legend_title_text": "유저 타입"
    },
    height = 500 
)

## Step.4 - 그래프 마우스 오버시 hovermode x축으로 설정
fig.update_layout(hovermode="x")

## Step.5 - fig의 x축, y축 일괄 설정
fig.update_xaxes(title = "")
fig.update_yaxes(matches=None, showticklabels=True) # matches=None (y축을 독립적으로 설정)


## Step.6 - 그래프 출력
fig.show()

> **Comment**

- 11월을 기준으로 다판다마켓 공급 상품에 대한 기존 매장의 SALES와 PU를 유저 타입별로 나누어 살펴보면
- 메이비카페를 제외한 나머지 네 개 매장 모두 각 지표의 과반 이상이 재방문 유저로 부터 발생되는 것을 확인
- **앞서 살펴본 기존 유저들의 'MAU 볼륨 감소 방어' 및 '잔존율을 상승' 이슈와 연관지어 생각해보면** 
- **'신규상품이 기존유저들의 재유입/재구매를 야기하고 추가 매출을 발생시켰다.'는 가설 도출 가능**

In [ ]:
#@title Make DataFrame-2

## << monthlyNewProductCheckDf: 월별 판매등록 상품의 new/old 구분 >>
query_job = client.query("""
  with new_old_product as (
    -- product_title의 최초 등록 시점(월)을 기준으로 등록월에는 new, 등록월이 아닌 다른 월에는 old로 구분하는 쿼리
    select  product_title, registration_date, registration_year_month, first_registration_year_month
        , case when registration_year_month = first_registration_year_month then 'new'
                else 'old'
          end product_category
    from (
      select distinct product_title, registration_date, format_date('%Y-%m', registration_date) as registration_year_month
          , min(format_date('%Y-%m', registration_date)) over(partition by product_title) as first_registration_year_month
      from `localparm_dw.products` 
    ) as a
    order by product_title, registration_date
  )


  select registration_year_month, product_category, count(*) as registration_cnt
      , round(count(*)/sum(count(*)) over(partition by registration_year_month), 3) as ratio
  from new_old_product
  group by registration_year_month, product_category
  order by registration_year_month, product_category
""")

monthlyNewProductCheckDf = query_job.to_dataframe()

In [ ]:
#@title Visualization-4

## << 지역별 MAU - Bar Chart >>

import plotly.express as px

## Step.1 - fig에 px.bar() 그래프 담기
fig = px.bar(monthlyNewProductCheckDf, 
              x="registration_year_month", 
              y="ratio", 
              color= "product_category",
              text="ratio",
             )


# ## Step.2 - text 표현 형식과, 출력 위치를 조정 / 호버 텍스트 포멧 조정
fig.update_traces(texttemplate='%{text:.1%}', textposition='inside') 
fig.update_traces(hovertemplate = "상품 등록 비중: %{text:.1%}" )


# ## Step.3 - fig의 layout 설정 변경
fig.update_layout(
    {
        "title": {
            "text": "<b>< [별첨] 월별 신규상품 등록 비중 ><b>",
            "x": 0.5,
            "y": 0.95,
            "font": {
                "size": 13
            }
        },
        "xaxis": { 
            "title": "", 
            "tick0": "2022-04", 
            "dtick": "M1",
            "tickformat": "%Y-%m",
        },
        "yaxis": { "title": "매출비중(%)", "tickformat": '.0%' }, 
        "legend_title_text": "상품구분",
        "legend": { "traceorder": "normal"},
        "template":'plotly_white',
        "height": 300,
    }
)

## Step.4 - 그래프 마우스 오버시 hovermode x축으로 설정
fig.update_layout(hovermode="x")


## Step.5 - 그래프 출력
fig.show()

> **Note**

- 21년 7월 ~ 22년 4월 동안의 상품등록 데이터가 없어 정확한 신규상품/기존상품 분류는 아니므로 추세만 참고

> **Comment**

- 8월말 추석상품 판매로 인한 매출 상승분을 감안하고 본다면, 8월 ~ 11월 new 상품군의 등록 비중 추이와 월매출 증감 추이가 동일하게 움직이는 것을 확인

## < 매출 기여도 구성 현황 >

In [ ]:
#@title Make DataFrame-1

## << monthlySalesGrowthAccountDf: 월간 매출 성장 회계 데이터 >>
query_job = client.query("""
  with payment_log as (
      select order_date
          , order_year_month
          , format_date('%Y', order_date) as year_id
          , format_date('%m', order_date) as month_id
          , order_id, user_id, payment_amount
          , dense_rank() over(partition by user_id order by format_date('%Y', order_date), format_date('%m', order_date)) as payment_order
      from `my_temp.orders`
  ),

  payment_log_grouping as (
    select year_id, month_id, order_year_month, user_id
        , sum(payment_amount) as sales
        , dense_rank() over(order by year_id, month_id) as time_order
        , count(distinct order_id) as payment_cnt
        , min(payment_order) as payment_order
    from payment_log
    group by year_id, month_id, order_year_month, user_id
  ),

  payment_group as (
    select a.year_id, a.month_id, a.order_year_month, a.time_order
        , case when a.payment_order = 1 then 'new_user' -- 22년 4월 이후 (첫 결제 유저)
              when b.user_id is not null then 'retained_user' -- 지난달과 해당월에 모두 결제한 유저
              when b.user_id is null then 'resurrected_user' -- 이번달에 결제했고, 지난달은 결제하지 않았지만 이전에 결제가 있었던 유저
              else 'none'
          end as user_group
        , count(distinct a.user_id) as payment_user_cnt
        , sum(a.sales) as payment_amount
    from payment_log_grouping as a
    left join payment_log_grouping as b -- 전월 결제여부 체크
    on a.user_id = b.user_id and (a.time_order - 1) = b.time_order
    group by a.year_id, a.month_id, a.order_year_month, a.time_order
          , case when a.payment_order = 1 then 'new_user' -- 21년 6월 이후 (첫 결제 유저)
                  when b.user_id is not null then 'retained_user' -- 지난달과 해당월에 모두 결제한 유저
                  when b.user_id is null then 'resurrected_user' -- 지난달과 해당월에 모두 결제한 유저
                  else 'none'
            end
  ),

  payment_churn_group as (
    select a.year_id, a.month_id, a.order_year_month, a.time_order
        , case when b.user_id is not null then 'else' --'retained_user' 
              when b.user_id is null then 'churned_user'
                else 'none'
          end as user_group
        , count(distinct a.user_id) as payment_user_cnt
        , sum(a.sales) as payment_amount
    from payment_log_grouping as a
    left join payment_log_grouping as b
    on a.user_id = b.user_id and (a.time_order +1) = b.time_order
    group by a.year_id, a.month_id, a.order_year_month, a.time_order
          , case when b.user_id is not null then 'else' 
                  when b.user_id is null then 'churned_user'
                  else 'none'
            end
  ),

  payment_churn_group_re as (
    select b.year_id, b.month_id, b.order_year_month, a.user_group, a.payment_user_cnt, a.payment_amount
    from (
      select year_id, month_id, order_year_month, user_group, payment_user_cnt, payment_amount, time_order
      from payment_churn_group
    ) as a
    left join (
      select distinct year_id, month_id, order_year_month, time_order
      from payment_group
    ) as b
    on (a.time_order + 1) = b.time_order
  )

  select year_id, month_id, order_year_month as year_month, user_group
      , case when key_id = 'churn' then (- payment_user_cnt) else payment_user_cnt end as payment_user_cnt
      , case when key_id = 'churn' then (- payment_amount)  else payment_amount  end as payment_amount 
  from(
    select year_id, month_id, order_year_month, user_group, payment_user_cnt, payment_amount, 'default' as key_id 
    from payment_group
    
    union all 
    
    select year_id, month_id, order_year_month, user_group, payment_user_cnt, payment_amount, 'churn' as key_id  
    from payment_churn_group_re
    where user_group= 'churned_user'
  ) as a
  where order_year_month is not null
  order by year_id, month_id, user_group
""")
monthlySalesGrowthAccountDf = query_job.to_dataframe()

In [ ]:
#@title Visualization-1

## << 장표: SALES Growth Accounting  >> 
import plotly.express as px

fig = px.bar(monthlySalesGrowthAccountDf[['year_month', 'user_group', 'payment_amount']], 
             x=monthlySalesGrowthAccountDf['year_month'], 
             y=monthlySalesGrowthAccountDf['payment_amount'],
             text=monthlySalesGrowthAccountDf['payment_amount'],
             color=monthlySalesGrowthAccountDf['user_group'])

fig.update_layout(
    {
        "title": {
            "text": "<b>< SALES - Growth Accounting ><b>",
            "x": 0.5,
            "y": 0.9,
            "font": {
                "size": 13
            }
        },
        "yaxis": {
            "title": "SALES"    
        },
        "xaxis": {
            "title": "",
            "tick0": "2022-02",
            "dtick": 'M1',
            "tickformat": "%Y-%m"
        },
        "template":'plotly_white',
        "legend_traceorder": "reversed",
        "legend_title_text": "사용자 그룹"
    }
)

fig.update_traces(textposition='inside', texttemplate='%{text:,}원',) # 왜 bar에서 안하고 여기서 하는지. https://plotly.com/python/text-and-annotations/

# fig.update_layout(legend_title_text='Legend title')
# fig.update_layout(legend_traceorder="reversed") # 범례 순서 정렬 (stack bar의 쌓이는 순서를 바꾸지는 않는듯)
# fig.update_layout(xaxis={'categoryorder':'total ascending'}) # categoryorder << 지금 여기서 쓰지는 않았는데.. 딱히 적용되는 걸 확인하지도 못함.

fig.show()

> **Note**

- 사용자 그룹 정의
  - new_user : 22년 4월 이후 첫 결제 유저
  - retained_user : 지난달과 이번달에 모두 결제한 유저
  - resurrected_user : 이번달에 결제했고, 지난달은 결제하지 않았지만 이전에 결제이력이 있는 유저
  - churned_user : 전월에 결제를 했지만, 이번달에 결제를 안한 유저(해당 유저들이 직전월에 얼만큼 구매를 했는지 확인하기 위함)

> **Comment**

- 11월 기준, new 그룹의 매출은 역대 최고 수준인 8천만원을 달성했으며 재구매 유저그룹인 retained, resurrected 그룹 또한 각각 전월比 49%, 27% 상승
- 기존 유저들의 재구매 전환 상승의 영향으로 churned 그룹 또한 역대 최저 수준인 1천만원으로 집계

In [ ]:
#@title Make DataFrame-2 ⛳️

## << monthlySalesGrowthAccountByRePurchaseGroupDf: 월간 매출 성장 회계 데이터 - retained, resurrected 그룹의 로컬팜/다판다마켓 판매상품 구매 비교 >>
query_job = client.query("""

  with payment_log as (
      select a.order_date
           , a.order_year_month
           , format_date('%Y', a.order_date) as year_id
           , format_date('%m', a.order_date) as month_id
           , a.order_id, a.user_id, a.payment_amount
           , c.nickname as seller_nickname
           , case when c.nickname = '김정식-2cca8b6e' then '다판다마켓셀러' 
                  else '로컬팜셀러'
             end as seller_category
           , dense_rank() over(partition by a.user_id order by format_date('%Y', a.order_date), format_date('%m', a.order_date)) as payment_order
      from `my_temp.orders` as a
      -- 상품 정보를 붙인다.(판매자 정보를 붙이기 위한 사전 작업)
      left join `localparm_dw.products` as b
      on a.product_id = b.product_id
      -- 판매자 정보를 붙인다.
      left join `my_temp.my_infos` as c 
      on b.user_id = c.user_id
  ),

  payment_log_grouping as (
    select year_id, month_id, order_year_month, user_id
        , sum(payment_amount) as sales
        , dense_rank() over(order by year_id, month_id) as time_order
        , count(distinct order_id) as payment_cnt
        , min(payment_order) as payment_order
    from payment_log
    group by year_id, month_id, order_year_month, user_id
  ),

  payment_group as (
    select a.year_id, a.month_id, a.order_year_month, a.time_order, a.user_id
        , case when a.payment_order = 1 then 'new_user' -- 22년 4월 이후 (첫 결제 유저)
              when b.user_id is not null then 'retained_user' -- 지난달과 해당월에 모두 결제한 유저
              when b.user_id is null then 'resurrected_user' -- 이번달에 결제했고, 지난달은 결제하지 않았지만 이전에 결제가 있었던 유저
              else 'none'
          end as user_group
    from payment_log_grouping as a
    left join payment_log_grouping as b -- 전월 결제여부 체크
    on a.user_id = b.user_id and (a.time_order - 1) = b.time_order
  )


  select a.order_year_month, b.user_group, a.seller_category
       , sum(a.payment_amount) as sales
       , count(distinct a.user_id) as pu
  from (
    select order_date, order_year_month, user_id, payment_amount
         , seller_nickname
         , seller_category
    from payment_log
  ) as a
  inner join (
    select distinct order_year_month, user_id, user_group
    from payment_group
    where user_group in ('retained_user', 'resurrected_user')
  ) as b
  on  a.user_id = b.user_id and a.order_year_month = b.order_year_month
  group by a.order_year_month, b.user_group, a.seller_category
  order by a.order_year_month, b.user_group, a.seller_category
""")

monthlySalesGrowthAccountByRePurchaseGroupDf = query_job.to_dataframe()

In [ ]:
#@title Visualization-2 ⛳️

## << 김정식님(다판다마켓 셀러) 판매상품에 대한 기존 유저들의 구매 현황 >>

import plotly.express as px

## step.1 - fig에 px.line() 그래프 담기
fig = px.bar(monthlySalesGrowthAccountByRePurchaseGroupDf, 
              x="order_year_month", 
              y= "sales", 
              color="seller_category",
              text="sales",
              facet_col = "user_group",
              facet_col_spacing = 0.1, #  (float between 0 and 1) – Spacing between facet rows, in paper units. Default is 0.03 or 0.07 when facet_col_wrap is used.
              )

## step.2 - update_traces를 통한 text 표기 방식 설정
fig.update_traces(textposition='inside', texttemplate='%{text:,}원',) 

## Step.3 - fig의 layout 설정 변경
fig.update_layout(
    {
        "title": {
            "text": "<b>< 재구매 유저 - 다판다마켓 상품 구매액 비교 ><b>",
            "x": 0.5,
            "y": 0.99,
            "font": {
                "size": 15
            }
        },
        "yaxis1": {
            "title": "SALES(원)",
            "tickformat": ","
        },
        "yaxis2": {
            "title": "SALES(원)",
            "tickformat": ","
        },
        "legend_title_text": "판매자 구분"
    },
    height = 500 
)

## Step.4 - 그래프 마우스 오버시 hovermode x축으로 설정
fig.update_layout(hovermode="x")

## Step.5 - fig의 x축, y축 일괄 설정
fig.update_xaxes(title = "", tick0 = "2022-06", dtick = 'M1', tickformat = "%Y-%m")
fig.update_yaxes(matches=None, showticklabels=True) # matches=None (y축을 독립적으로 설정)


## Step.6 - 그래프 출력
fig.show()

> **Comment**

- 앞서 살펴본 매출 상승이 신규상품 공급에 인한 영향인지 살펴보기 위해 재구매 유저 그룹의 매출을 판매자 기준으로 나누어 살펴보면
- 11월 재구매 유저그룹(retained, resurrected) 모두 매출의 약 25%가 다판다마켓 상품으로부터 발생됨을 확인

# **[ 구매형태 분석 ]**

## < 요약 ✨ >

> **매장별 구매형태 비교**
  - 11월 결제 데이터를 기준으로 매장별 구매형태는 유사하며 과반 이상의 결제 유저가 한달에 4만원 이하 또는 2회 이하로 상품을 구매
  - 메이비카페점을 제외한 나머지 7개 매장의 경우, 구매유저의 90% 이상이 거주지와 매장간의 거리가 1km 이하로 측정되며 거리와 누적 구매액간의 상관성은 발견하지 못함
  - 메이비카페점은 거주지와 매장간의 거리가 5km를 넘는 경우가 전체 결제유저의 31%를 차지

## < 매장별 구매 형태 비교 >

In [ ]:
!pip install haversine ## 두 좌표간 직선거리를 구하기 위한 패키지 설치

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
#@title Make DataFrame ⛳️

## << novSalesInfoByShopDf: 11월 매장별 유저별 구매횟수, 구매액 >>
query_job = client.query("""
  select pickup_shop_name, user_id, count(distinct order_id) as purchase_cnt, sum(payment_amount) AS sales
  from `my_temp.orders`
  where order_year_month = '2022-11'
    and payment_status = 'completed'
  group by pickup_shop_name, user_id
  order by pickup_shop_name, SALES desc
""")
novSalesInfoByShopDf = query_job.to_dataframe()

# << distBetweenLocalAndShopDf : 11월 구매유저 - 주거지 <-> 매장 거리 분포 >>
query_job = client.query("""
  select a.user_id, a.pickup_shop_name, a.sales
      , case when a.sales <= 10000 then 'g_1만원'
             when a.sales <= 20000 then 'g_1만원_2만원'
             when a.sales <= 30000 then 'g_2만원_3만원'
             when a.sales <= 40000 then 'g_3만원_4만원'
             else 'g_4만원_more'
        end user_group
      , trunc(b.x, 3) as home_x, trunc(b.y, 3) as home_y
      , trunc(c.x, 3) as shop_x, trunc(c.y, 3) as shop_y
  from (
    select distinct user_id, pickup_shop_name, sum(payment_amount) as sales
    from `my_temp.orders`
    where order_year_month = '2022-11'
      and payment_status = 'completed'
    group by user_id, pickup_shop_name
  ) as a
  left join (
    select distinct user_id, region_3depth_name as region, h_code, x, y
    from `my_temp.my_infos`
  ) as b
  on a.user_id = b.user_id
  left join (
    select distinct pickup_shop_name, h_code, x, y
    from `localparm_dw.pickup_shop`
  ) as c
  on a.pickup_shop_name = c.pickup_shop_name
""")
distBetweenLocalAndShopDf = query_job.to_dataframe()


## << 데이터 변환: 11월 픽업상품 구매 유저의 (매장 <-> 설정지역)간의 거리 계산 >>

##  latitude(위도) = x, longitude(경도) = y

from haversine import haversine

#--------------------------------------------------------------
# (haversine() 연산을 위해, 픽업장소와, 본인지역에 대한 위도와 경도를 ('', '')
#--------------------------------------------------------------

## 이렇게 스트링으로 넣어주면 안되고
# novPickupUniquePu['pickup_location'] = novPickupUniquePu[['pickup_lat', 'pickup_long']].apply(lambda row: '(' + ', '.join(row.values.astype(str)) + ')', axis=1)
# novPickupUniquePu['preferred_location'] = novPickupUniquePu[['preferred_lat', 'preferred_long']].apply(lambda row: '(' + ', '.join(row.values.astype(str)) + ')', axis=1)

## 이렇게 튜플 형태로 좌표를 묶어서 넣어줘야, 밑에서 havershine() 함수가 작동함 🔥
distBetweenLocalAndShopDf['pickup_location'] = distBetweenLocalAndShopDf[['shop_x', 'shop_y']].apply(lambda x: (x['shop_x'], x['shop_y']), axis=1)
distBetweenLocalAndShopDf['home_location'] = distBetweenLocalAndShopDf[['home_x', 'home_y']].apply(lambda x: (x['home_x'], x['home_y']), axis=1)


#--------------------------------------------------------------
# (본인이 설정한 동네 위치와, 픽업 장소 위치간의 km 계신)
#--------------------------------------------------------------

def calculateDistance(x):
    return haversine(x[0], x[1], unit = 'km')
    
distBetweenLocalAndShopDf['distance'] = distBetweenLocalAndShopDf[['home_location', 'pickup_location']].apply(calculateDistance, axis=1) 

In [ ]:
#@title Visualization-1 ⛳️
fig = px.histogram(novSalesInfoByShopDf, x="sales", color="pickup_shop_name", 
                   marginal="box", # can be rug, box, violin
                   histnorm='percent', #percent, probability, density
                   barmode='overlay', # stack, group, overlay
                   hover_data=novSalesInfoByShopDf.columns)

fig.update_layout(
    {
        "title": {
            "text": "<b>< 11월 결제유저의 매장별 누적 구매액 분포 ><b>",
            "x": 0.5,
            "y": 0.95,
            "font": {
                "size": 13
            }
        },
    },
)

fig.update_xaxes(title="월간 누적 구매액", row=1)

fig.show()


# << Def. lower fence & upper fence >>
# The lower fence is at x = Q1 - 1.5 * IQR
# The upper fence is at x = Q3 + I.5 * IQR
# The IQR is the interquartile range: IQR = Q3 - Q1

#  << barmode >>
#  "stack" : bars are stacked on top of one another
#  "group" : bars are next to one another
#  "overlay": bars are plotted over one another

# << histnorm >>
# Type of normalization
# The default mode is to represent the count of samples in each bin. 
# With the histnorm argument, it is also possible to represent the percentage or fraction of samples in each bin (histnorm='percent' or probability), 
# or a density histogram (the sum of all bar areas equals the total number of sample points, density), 
# or a probability density histogram (the sum of all bar areas equals 1, probability density).

> **Note**

- 매장별 분포비교를 위해 히스토그램의 Y축 스케일이 동일한 수준(%)으로 변경됨

> **Comment**

- **8개 매장의 월간 누적 구매액 중앙값 평균은 약36,000원 수준이며, 한달에 4만원 이하를 구매하는 유저가 전체 구매 유저의 약50%를 차지**
- 표본이 적은 더현대서울지점을 제외하고 7개 매장별 누적구매액 분포 형태는 대동소이함

In [ ]:
#@title Visualization-2

fig = px.histogram(novSalesInfoByShopDf, x="purchase_cnt", color="pickup_shop_name", marginal="box", # can be rug, box, violin
                   histnorm='percent', #percent, probability, density
                   barmode='overlay', # stack, group, overlay
                   hover_data=novSalesInfoByShopDf.columns)

fig.update_layout(
    {
        "title": {
            "text": "<b>< 11월 결제유저의 매장별 누적 구매횟수 분포 ><b>",
            "x": 0.5,
            "y": 0.95,
            "font": {
                "size": 13
            }
        },
    },
)

fig.update_xaxes(title="월간 누적 구매 횟수", row=1)
fig.show()

> **Note**

- 매장별 분포비교를 위해 히스토그램의 Y축 스케일이 동일한 수준(%)으로 변경됨

> **Comment**

- **8개 매장의 월간 누적 구매 횟수 중앙값 평균은 약2.4회 이며, 월간 구매 횟수가 2회 이하인 유저가 전체 구매 유저의 약 46~55%를 차지**
- 표본이 적은 더현대서울지점을 제외하고 7개 매장별 누적 구매횟수 분포 형태는 대동소이함

In [ ]:
#@title Visualization-3

fig = px.histogram(distBetweenLocalAndShopDf, x="distance", color="pickup_shop_name", marginal="box", # can be rug, box, violin
                  #  histnorm='percent', #percent, probability, density
                   barmode='overlay', # stack, group, overlay
                   hover_data=distBetweenLocalAndShopDf.columns)

fig.update_layout(
    {
        "title": {
            "text": "<b>< 11월 결제유저의 매장별 거리(거주지 ↔ 매장) 분포 ><b>",
            "x": 0.5,
            "y": 0.98,
            "font": {
                "size": 13
            }
        },
        "height": 500,
    },
)

fig.update_xaxes(title="거주지 ↔ 매장 거리(km)", row=1)
fig.show()

> **Note**

- 매장별 분포비교를 위해 히스토그램의 Y축 스케일이 동일한 수준(%)으로 변경됨

> **Comment**

- 결제유저의 거주지로부터 매장까지의 거리 분포를 살펴보면, 매장별로 다소 차이가 있으며 
- **특히 메이비카페의 경우 거리가 5km가 넘는 결제유저가 약 31%인 것으로 보아 출퇴근 길 사용자들이 다수 있을 것으로 예상됨**
- **또한, 메이비카페 지점을 제외하면 7개지점 모두 거주지와 매장간의 거리가 1km 이하 인것으로 보아 구매 전환 가능한 심리적 마지노선이 최대 1km로 추정됨**

In [ ]:
#@title Visualization-4

fig = px.histogram(distBetweenLocalAndShopDf, x="distance", color="pickup_shop_name", marginal="box", # can be rug, box, violin
                   histnorm='percent', #percent, probability, density
                   barmode='overlay', # stack, group, overlay
                   facet_col = "user_group",
                   category_orders={"user_group": ["g_1만원", "g_1만원_2만원", "g_2만원_3만원", "g_3만원_4만원", 'g_4만원_more']},
                   hover_data=distBetweenLocalAndShopDf.columns)

fig.update_layout(
    {
        "title": {
            "text": "<b>< 누적 과금 수준에 따른 - 11월 결제유저의 매장별 거리(거주지 ↔ 매장) 분포 ><b>",
            "x": 0.5,
            "y": 0.99,
            "font": {
                "size": 13
            }
        },
    },
)

fig.update_xaxes(title="거주지 ↔ 매장 거리(km)", row=1)
fig.show()

> **Note**

- 매장별 분포비교를 위해 히스토그램의 Y축 스케일이 동일한 수준(%)으로 변경됨

> **Comment**

- **누적구매액이 높을수록 거주지와 매장간의 거리가 가까운지 살펴보았으나 특이점을 발견하지 못함**
- 결제유저 객단가에 영향을 미치는 요인에 대해서는 거리 외의 다른 요인 추가 탐색이 필요